

#Escrapeo Airbnb



###0 - Instaladores y librerías

In [1]:
# Instalaciones necesarias
!pip install selenium
!pip install fake_useragent

# Importación de librerías
import pandas as pd  # Manejo de dataframes
import numpy as np  # Operaciones matemáticas y matrices
import re  # Para modificar textos con buscar y reemplazar
import time  # Manejo del tiempo
import requests  # Enviar solicitudes HTTP
import os  # Operaciones del sistema
import glob  # Buscar archivos en el sistema
import ast # Para poder usar una función que convierte listas "aparentes" en listas




from bs4 import BeautifulSoup as bs  # Parsear y manipular HTML
from selenium import webdriver  # Automatizar el navegador
from selenium.webdriver.common.by import By  # Selección de elementos HTML
from selenium.webdriver.support.ui import Select  # Manejo de menús desplegables
from selenium.webdriver.support.ui import WebDriverWait  # Espera hasta que un elemento esté disponible
from selenium.webdriver.support import expected_conditions as EC  # Condiciones para esperar en Selenium
from IPython.display import clear_output  # Limpiar la salida en Google Colab, para que las multiples ejecuciones no acomulen los multiple resultados
from fake_useragent import UserAgent  # Generar un user agent aleatorio para las solicitudes
from urllib.parse import urlparse, parse_qs  # urlparse puede descomponer las partes de una URL, y parse_qs genera diccionadores sobre los parametros de una URL
from datetime import datetime  # Manejo de fechas y horas

# Configuración del navegador Chrome
from selenium.webdriver.chrome.options import Options  # Configuración del navegador Chrome, abriendo las siguientes opciones:
chrome_options = Options()
chrome_options.add_argument('--headless')  # Ejecuta el navegador en segundo plano (sin interfaz gráfica)
chrome_options.add_argument('--no-sandbox')  # Previene problemas de permisos en entornos protegidos
chrome_options.add_argument('--disable-dev-shm-usage')  # Optimiza el uso de memoria compartida

# Montar Google Drive
from google.colab import drive
from google.colab import files  # Cargar y descargar archivos en Google Colab
drive.mount('/content/drive')  # Monta Google Drive en Colab para leer/escribir archivos

import warnings #Evitamos los mensajes warning
warnings.filterwarnings('ignore')


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.5/9.5 MB 42.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 492.9/492.9 kB 24.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 201.1/201.1 kB 4.3 MB/s eta 0:00:00
Mounted at /content/drive


###2 - EXTRACTOR DATOS GLOBAL.



####2.0 Agentes, URLs

In [ ]:
# Configuración del agente de usuario falso
ua = UserAgent()
chrome_options.add_argument(f'user-agent={ua.random}')
# Inicialización del driver de Chrome
driver = webdriver.Chrome(options=chrome_options)

Dict_capitales = {
    1: 'albacete',
    2: 'alicante',
    3: 'almeria',
    4: 'avila',
    5: 'badajoz',
    6: 'barcelona',
    7: 'bilbao',
    8: 'burgos',
    9: 'caceres',
    10: 'cadiz',
    11: 'castellon',
    12: 'ceuta',
    13: 'ciudadreal',
    14: 'cordoba',
    15: 'coruna',
    16: 'cuenca',
    17: 'donostia',
    18: 'girona',
    19: 'granada',
    20: 'guadalajara',
    21: 'huelva',
    22: 'huesca',
    23: 'jaen',
    24: 'leon',
    25: 'lleida',
    26: 'logrono',
    27: 'lugo',
    28: 'madrid',
    29: 'malaga',
    30: 'melilla',
    31: 'merida',
    32: 'murcia',
    33: 'ourense',
    34: 'oviedo',
    35: 'palencia',
    36: 'palma',
    37: 'pamplona',
    38: 'pontevedra',
    39: 'salamanca',
    40: 'santander',
    41: 'santiagodecompostela',
    42: 'segovia',
    43: 'sevilla',
    44: 'soria',
    45: 'tarragona',
    46: 'teruel',
    47: 'toledo',
    48: 'valencia',
    49: 'valladolid',
    50: 'vitoria',
    51: 'zamora',
    52: 'zaragoza'
}




##### FUNCIONES #####

### Conversor de decimal a tiempo
def conversor_horas(hora_decimal):
    horas = int(hora_decimal)
    minutos = int((hora_decimal - horas) * 60)
    return f"{horas:02d}:{minutos:02d}"


### Cerrar pops de traducción y cookies
def cerrar_popups(driver):
    try:
        boton_traduccion = WebDriverWait(driver, 1).until(
            EC.element_to_be_clickable((By.XPATH, '/html/body/div[9]/div/div/section/div/div/div[2]/div/div[1]/button'))
        )
        boton_traduccion.click()
        print("Ha saltado pop de traducción automática, lo cerramos")
    except:
        print("No ha saltado pop de traducción automática")

    try:
        boton_cookies = WebDriverWait(driver, 1).until(
            EC.element_to_be_clickable((By.XPATH, "//button[contains(text(), 'Solo las necesarias')]"))
        )
        boton_cookies.click()
        print("Ha saltado pop de galletas, lo cerramos")
    except:
        print("No ha saltado pop de galletas")



### Cargar el progreso parcial de escrapeo, en archivos que incluyen N anuncios
def cargar_archivos_parciales(ruta_guardado):

    # Con os.path.join, me defino la ruta en la que estarán los archivos, indicando que los archivos empiezan por df_parcial_
    # Con glob.glob() busco archivos en el directorio que coincidan con el patrón especifico, en este caso, el definido en os.path.join
    # Me crea una lista de todos los archivos que coinciden con ese patrón
    archivos_parciales = glob.glob(os.path.join(ruta_guardado, "df_parcial_*.csv"))

    if archivos_parciales:
        # Leo cada archivo csv y lo meto como dataframe en una lista (cada posicion almacena un dataframe)
        df_list = [pd.read_csv(file) for file in archivos_parciales]
        # Combino todos los dataframes de la lista en uno solo
        df_combinado = pd.concat(df_list, ignore_index=True)
        # Borro filas duplicadas
        df_combinado.drop_duplicates(subset=['URL'], inplace=True)
        # Guardar el DataFrame combinado en un archivo CSV
        archivo_combinado = os.path.join(ruta_guardado, "df_parcial_combinado.csv")
        df_combinado.to_csv(archivo_combinado, index=False)
        print(f"Archivo combinado guardado en: {archivo_combinado} con longitud {len(df_combinado['URL'])}")
        # Borro todos los parciales temporales para evitar que se acomulen
        archivos_parciales_temp = glob.glob(os.path.join(ruta_guardado, "df_parcial_temp*.csv"))
        for file in archivos_parciales_temp:
            os.remove(file)
            print(f"\nArchivo temporal eliminado: {file}")

        # Si no encuentra archivos parciales, devuelve dataframe vacío.
        return df_combinado

    return pd.DataFrame()  # Retorna un DataFrame vacío si no hay archivos


### Guardar el progreso parcial del escrapeo individual cada N anuncios
def guardar_parcial(dict_BASE, contador_iteracion):
    # Cada 20 iteraciones, se guarda el DataFrame en un CSV temporal, de nombre df_parcial
    if contador_iteracion % 10 == 0:
        # Creo df y quitamos las filas que contengan Nan
        df_parcial = pd.DataFrame(dict_BASE)
        df_parcial = df_parcial.dropna()
        # Añado al final del csv un sufijo con el contador y fecha para no sobreescribir el archivo
        file_path = f"/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/01.Temporales/df_parcial_temp{contador_iteracion}_{datetime.now()}.csv"
        df_parcial.to_csv(file_path, index=False)
        print(f"\nGuardado parcial tras {contador_iteracion} iteraciones.\n")


### Elección destino
def eleccion_destino():
  print(f"Vamos a proceder a la elección del lugar de destino")
  auxiliar = 0
  while auxiliar==0:
    print("\nPor favor, pulse el número correspondiente a la opción deseada:\n")
    for key, value in Dict_capitales.items():
      print(f"{key}: {value.capitalize()}")
    eleccion = int(input("\nSeleccione el número de la ciudad: "))

    if eleccion in Dict_capitales:
        ciudad_elegida = Dict_capitales[int(eleccion)].capitalize()
        print(f"\nUsted ha seleccionado {ciudad_elegida}")
        url_pre = "https://www.airbnb.es/s/"
        url_post = "-Spain/homes?refinement_paths%5B%5D=%2Fhomes"
        url_elegida = url_pre + ciudad_elegida + url_post
        url_elegida = [url_elegida]
        print(url_elegida)

        auxiliar = 1  # Salir del bucle
    else:
        print("Entrada no válida. Inténtelo de nuevo.")


  print(f"\nVamos a proceder al escrapeo de los alojamientos encontrados, por favor, espere a que termine el proceso.")

  return url_elegida

# Función de scroll hasta final de página
def scroll_to_bottom_slowly(driver, pause_time=2, step=500, screenshot_prefix="scroll_step"):
    """
    Realiza scroll hasta el final de la página lentamente y guarda pantallazos en cada iteración.

    :param driver: Instancia del WebDriver de Selenium.
    :param pause_time: Tiempo en segundos para esperar después de cada scroll parcial.
    :param step: Cantidad de píxeles para desplazarse en cada paso.
    :param screenshot_prefix: Prefijo para nombrar los pantallazos guardados en cada iteración.
    """
    last_height = driver.execute_script("return document.body.scrollHeight")
    current_position = 0
    iteration = 1  # Contador de iteraciones

    while current_position < last_height:
        # Guardar un pantallazo al inicio de cada iteración
        # screenshot_name = f"{screenshot_prefix}_{iteration}.png"
        # driver.save_screenshot(screenshot_name)
        # print(f"Pantallazo guardado: {screenshot_name}")

        # Desplazar hacia abajo en incrementos
        driver.execute_script(f"window.scrollTo(0, {current_position});")
        current_position += step
        time.sleep(pause_time)  # Esperar para permitir la carga de contenido dinámico

        # Verificar si la altura de la página ha cambiado
        new_height = driver.execute_script("return document.body.scrollHeight")
        if new_height > last_height:
            last_height = new_height  # Actualizar la altura si la página se extiende

        iteration += 1  # Incrementar el contador de iteraciones

    # Hacer un scroll final para asegurarse de llegar al final
    driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")
    time.sleep(pause_time)




####2.0 Funciones de escrapeo

In [ ]:

#Función EXTRACCIÓN RATINGS
def extraer_ratings(soup, dict_BASE):
    """
    Extrae los ratings de limpieza, veracidad, llegada, comunicación, ubicación y calidad,
    así como el título del alojamiento y los guarda en un diccionario.

    Args:
        soup (BeautifulSoup): Objeto BeautifulSoup con el HTML de la página.
        dict_BASE (dict): Diccionario donde se almacenan los resultados.

    Returns:
        None: Modifica el dict_BASE directamente.
    """
    # En este extracto de sopa está el nombre del alojamiento
    sopa_titulo = soup.find('h1', {'class': 'hpipapi atm_7l_1kw7nm4 atm_c8_1x4eueo atm_cs_1kw7nm4 atm_g3_1kw7nm4 atm_gi_idpfg4 atm_l8_idpfg4 atm_kd_idpfg4_pfnrn2 i1pmzyw7 atm_9s_1nu9bjl dir dir-ltr'})
    sopa_ratings = soup.find_all('div', {'class': 'l925rvg atm_9s_1txwivl atm_ar_1bp4okc atm_cx_yh40bf dir dir-ltr'})

    # Extraer el título del alojamiento
    if sopa_titulo:
        titulo = sopa_titulo.get_text(strip=True)
        dict_BASE['Nombre Alojamiento'].append(titulo)
    else:
        dict_BASE['Nombre Alojamiento'].append(None)

    # Extraer ratings
    if sopa_ratings:
        keys = ['Rating Limpieza', 'Rating Veracidad', 'Rating Llegada', 'Rating Comunicacion', 'Rating Ubicacion', 'Rating Calidad']
        for i, key in enumerate(keys):
            extracto_sopa = sopa_ratings[i].get_text(strip=True)
            numero_extraido = re.findall(r'\d+\.\d+|\d+', extracto_sopa)
            numero_unido = ''.join(numero_extraido)
            numero_formateado = numero_unido[:-1] + '.' + numero_unido[-1:]
            dict_BASE[key].append(float(numero_formateado))

        print(f"Desglose ratings: \n---Rating limpieza: {dict_BASE['Rating Limpieza'][-1]}\n---Rating Veracidad: {dict_BASE['Rating Veracidad'][-1]}\n---Rating Llegada: {dict_BASE['Rating Llegada'][-1]}\n---Rating Comunicación: {dict_BASE['Rating Comunicacion'][-1]}\n---Rating Ubicación: {dict_BASE['Rating Ubicacion'][-1]}\n---Rating Calidad: {dict_BASE['Rating Calidad'][-1]}")

    else:
        for key in ['Rating Limpieza', 'Rating Veracidad', 'Rating Llegada', 'Rating Comunicacion', 'Rating Ubicacion', 'Rating Calidad']:
            dict_BASE[key].append(None)

        nuevo = soup.find_all('div', {'class': 'r1lutz1s atm_c8_o7aogt atm_c8_l52nlx__oggzyc dir dir-ltr'})
        if nuevo:
            for elemento in nuevo:
                if elemento.text == "Nuevo":
                    print("Anuncio Nuevo, añadimos 'Nuevo' a Ratings")
                    for key in ['Rating Limpieza', 'Rating Veracidad', 'Rating Llegada', 'Rating Comunicacion', 'Rating Ubicacion', 'Rating Calidad']:
                        dict_BASE[key].pop()
                        dict_BASE[key].append("Nuevo")
                elif elemento.text == "Sin evaluaciones":
                    print("Anuncio Sin Evaluaciones, añadimos 'Nuevo' a Ratings")
                    for key in ['Rating Limpieza', 'Rating Veracidad', 'Rating Llegada', 'Rating Comunicacion', 'Rating Ubicacion', 'Rating Calidad']:
                        dict_BASE[key].pop()
                        dict_BASE[key].append("Nuevo")
        else:
            print("Desglose ratings: \n---No se encontraron ratings, añadimos n/a")


#Función DESCRIPCIÓN
def extraer_descripcion(driver, soup, dict_BASE):
    """
    Extrae la descripción de un alojamiento, detectando si hay un botón de traducción disponible
    y actualizando el diccionario con la descripción encontrada.

    Args:
        driver (webdriver): Objeto WebDriver de Selenium.
        soup (BeautifulSoup): Objeto BeautifulSoup con el HTML de la página.
        dict_BASE (dict): Diccionario donde se almacenan los resultados.

    Returns:
        None: Modifica el dict_BASE directamente.
    """
    try:
        # Detectar y hacer clic en el botón de traducción (si existe)
        boton_traduccion = driver.find_element(By.XPATH, "//button[starts-with(text(), 'Mostrar el')]")
        boton_traduccion.click()
        WebDriverWait(driver, 2).until(EC.presence_of_element_located((By.XPATH, '//span[@class="lrl13de atm_kd_19r6f69_24z95b atm_kd_19r6f69_1xbvphn_1oszvuo dir dir-ltr"]')))

        print("Encontrado el botón de traducción, buscamos ahora la descripción.")

        # Buscar contenido actualizado en la sopa
        sopa_desc = soup.find_all('span', {'class': 'lrl13de atm_kd_19r6f69_24z95b atm_kd_19r6f69_1xbvphn_1oszvuo dir dir-ltr'})

        if sopa_desc and len(sopa_desc) > 1:
            descripcion = sopa_desc[1].get_text(strip=True)
            dict_BASE['Descripcion'].append(descripcion)
        else:
            dict_BASE['Descripcion'].append('Hay traducción pero no encuentra descripción')

    except Exception as e:
        print("Sin presencia de traducción, añadimos descripción directamente.")
        # Buscar descripción directamente sin traducción
        sopa_desc = soup.find_all('span', {'class': 'lrl13de atm_kd_19r6f69_24z95b atm_kd_19r6f69_1xbvphn_1oszvuo dir dir-ltr'})

        if sopa_desc:
            descripcion = sopa_desc[0].get_text(strip=True)
            dict_BASE['Descripcion'].append(descripcion)
        else:
            dict_BASE['Descripcion'].append('Ni hay traducción ni encuentra descripción')



def extraer_maps(driver, url, dict_base, pause_time=2):
    """
    Extrae coordenadas desde un enlace de Google Maps presente en la página.

    :param driver: Instancia de WebDriver de Selenium.
    :param url: URL de la página a visitar.
    :param dict_base: Diccionario donde se almacenan los resultados de latitud y longitud.
    :param pause_time: Tiempo en segundos para esperar después del scroll.
    """
    try:
        # Cargar la página
        driver.get(url)
        time.sleep(2)

        # Scroll lento hasta el final de la página
        scroll_to_bottom_slowly(driver, pause_time=1, step=800)

        # Obtener el HTML de la página
        html = driver.page_source
        soup = bs(html, 'html.parser')

        # Buscar todos los enlaces en el HTML
        map_links = soup.find_all('a', href=True)

        # Filtrar enlaces que contengan 'google.com/maps' o '@'
        google_maps_links = [
            link['href'] for link in map_links
            if 'google.com/maps' in link['href'] or '@' in link['href']
        ]

        if google_maps_links:
            try:
                # Procesar el primer enlace encontrado
                href = google_maps_links[0]
                print(f"Enlace encontrado: {href}")

                # Analizar la URL
                parsed_url = urlparse(href)
                query_params = parse_qs(parsed_url.query)  # Extraer los parámetros de la URL

                # Buscar las coordenadas en el parámetro 'll'
                if 'll' in query_params:
                    coordenadas = query_params['ll'][0].split(',')  # Dividir latitud y longitud
                    latitud, longitud = coordenadas[0], coordenadas[1]
                    print(f"Latitud: {latitud}, Longitud: {longitud}")

                    # Guardar en el diccionario
                    dict_base['Latitud'].append(latitud)
                    dict_base['Longitud'].append(longitud)
                else:
                    print("No se encontraron coordenadas en el parámetro 'll'.")
                    dict_base['Latitud'].append(None)
                    dict_base['Longitud'].append(None)
            except Exception as e:
                print(f"Error al procesar el enlace: {e}")
                dict_base['Latitud'].append(None)
                dict_base['Longitud'].append(None)
        else:
            print("No se encontraron enlaces de Google Maps en el HTML.")
            dict_base['Latitud'].append(None)
            dict_base['Longitud'].append(None)



    except Exception as e:
        print(f"Error inesperado: {e}")
        driver.save_screenshot('error_general.png')
        dict_base['Latitud'].append(None)
        dict_base['Longitud'].append(None)

def invocar_demonio():
    print("""
           __     __
          /  \\---/  \\
         /    o o    \\
        (      ^      )
         \\    \\_/    /
          \\_________/
          /   /  \\   \\
         /   /    \\   \\
        /   /      \\   \\
       (   (        )   )
        \\   \\      /   /
         \\   \\    /   /
          \\___\\__/___/
             |    |
             |    |
            /      \\
           /        \\
          /          \\
         (            )
          \\__________/
    """)


####2.1 Conteo y recopilación de anuncios

En primer lugar, previo a recopilar la información completa de cada anuncio en particular, es preciso determinar el listado de los anuncios disponibles para cada ubicación que nos resulta de interés.

Por lo tanto, accediendo a las páginas de busqueda de alojamientos para la ubicación, recopilaremos los alojamientos que en ellas aparezcan listados. En este punto, obtendremos ya una información valiosa como viene a ser: precio por noche, valoración media del alojamiento, nombre de la ciudad y la ID del alojamento.

Este último valor resulta crucial ya que a partir de él definimos la URL que nos permitirá posteriormente acceder al anuncio de forma individualizada para escrapearlo.

In [ ]:
3# Creamos listas para los datos que necesitamos de las paginas de busqueda de airbnb
titulos = []
titulos2 = []
precios = []
rating = []
apartment_id = []
ciudad = []

# Llamamos a la función de seleccionar el destino a escrapear
destino_elegido = eleccion_destino()
contador_vueltas = 0
# Preguntamos cuántas vueltas queremos darle
vueltas_seleccionadas = int(input("\n¿Cuántas vueltas quieres darle al bucle? "))

while contador_vueltas < vueltas_seleccionadas:
# Bucle que va a iterar sobre cada una de las ciudades-url seleccionadas
    if contador_vueltas == 0:
        print("\nArrancando motores..., comenzamos!")
    else:
        print("\n¡Espera maño! Que le vamos a dar otra vuelta!\n")
        # driver.quit()
        # time.sleep(3)  # Asegurarse de que el proceso se haya cerrado completamente

        # Cambiar User-Agent y abrir nuevo navegador
        # ua = UserAgent()
        # chrome_options = webdriver.ChromeOptions()
        # driver = webdriver.Chrome(options=chrome_options)
    for url in destino_elegido:
        # Cargamos url y le damos unos segundos para que se complete
        driver.get(url)
        WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.XPATH, '//div[@data-testid="listing-card-title"]')))
        # En la página haremos lo siguiente hasta que no se pueda continuar
        while True:
            # Intentamos extraer la información y cuando de error nos lo devuelve
            try:
                # Extraer título
                titulos_anuncios = driver.find_elements(By.XPATH, '//div[@data-testid="listing-card-title"]')
                for titulo in titulos_anuncios:
                    titulos.append(titulo.text)

                # Extraer título2
                titulos_anuncios = driver.find_elements(By.XPATH, '//meta[@itemprop="name"]')
                for titulo in titulos_anuncios:
                    titulos2.append(titulo.get_attribute('content'))

                # Extraer precios
                precios_anuncios = driver.find_elements(By.XPATH, '//span[@class="_11jcbg2"]')
                for precio in precios_anuncios:
                    precios.append(precio.text)

                # Extraer ratio/nota
                rating_anuncios = driver.find_elements(By.XPATH, '//div[@class="t1a9j9y7 atm_da_1ko3t4y atm_dm_kb7nvz atm_fg_h9n0ih dir dir-ltr"]')
                for rate in rating_anuncios:
                    rating.append(rate.text)

                # Extraer IDs de anuncios
                soup = bs(driver.page_source, 'html.parser')
                for a_tag in soup.find_all('a', attrs={'aria-labelledby': True}): # Busca todos los enlaces (<a>) que tienen el atributo aria-labelledby.
                    aria_label = a_tag['aria-labelledby'] # Extrae el valor de aria-labelledby de cada enlace
                    # Si el valor de aria-labelledby empieza con "title_", toma lo que está después de "title_" y lo añade a una lista apartment_id
                    if aria_label.startswith('title_'):
                        aria_id = aria_label[len('title_'):]
                        apartment_id.append(aria_id)
                        ciudad_elegida = destino_elegido[0][24:]
                        ciudad_elegida = ciudad_elegida.split('/')[0]
                        ciudad_elegida = ciudad_elegida.replace("-Spain", "")
                        ciudad.append(ciudad_elegida)

                # Intentar encontrar el botón "Siguiente" y si no existe paramos todo el bucle porque ya hemos encontrado todos los anuncios que nos proporciona Airbnb
                try:
                    boton_siguiente = driver.find_element(By.XPATH, "//a[@aria-label='Siguiente']")
                    # Resumen de lo encontrado
                    print(f"Hemos encontrado:\n {len(titulos)} títulos\n {len(titulos2)} títulos2\n {len(precios)} precios \n {len(rating)} rating \n {len(apartment_id)} apartment_id \n {len(ciudad)} ciudades")
                    if len(titulos) == 666:
                        print("\nLlamando al diablo....\n")
                        invocar_demonio()
                    # SI llegado a un botón siguiente las listas tienen distinto len no podremos continuar, posible mensaje de aviso:
                    if not (len(titulos) == len(titulos2) == len(precios) == len(rating) == len(apartment_id) == len(ciudad)):
                        longitud_minima = min(len(titulos), len(titulos2), len(precios), len(rating), len(apartment_id), len(ciudad))

                        print("Error: Las listas no tienen la misma longitud.")
                        titulos = titulos[:longitud_minima]
                        titulos2 = titulos2[:longitud_minima]
                        precios = precios[:longitud_minima]
                        rating = rating[:longitud_minima]
                        apartment_id = apartment_id[:longitud_minima]
                        ciudad = ciudad[:longitud_minima]
                        continue  # Continuamos con el siguiente ciclo
                    # Hacer clic en el botón "Siguiente" y tiempo de espera
                    boton_siguiente.click()
                    time.sleep(3)
                except:
                    # Si no se encuentra el botón "Siguiente", hemos llegado al final
                    print("\nYa tenemos todos!:")
                    print(f"\n {len(titulos)} títulos\n {len(titulos2)} títulos2\n {len(precios)} precios \n {len(rating)} rating \n {len(apartment_id)} apartment_id \n {len(ciudad)} ciudades")
                    contador_vueltas += 1
                    if contador_vueltas == vueltas_seleccionadas:
                        print("\n¡Hemos llegado al final! ahora sí :-)")
                        break
                    break

            # Si da error que nos diga cual es
            except Exception as e:
                print(f"Se ha producido un error: {e}")
                break



Vamos a proceder a la elección del lugar de destino

Por favor, pulse el número correspondiente a la opción deseada:

1: Albacete
2: Alicante
3: Almeria
4: Avila
5: Badajoz
6: Barcelona
7: Bilbao
8: Burgos
9: Caceres
10: Cadiz
11: Castellon
12: Ceuta
13: Ciudadreal
14: Cordoba
15: Coruna
16: Cuenca
17: Donostia
18: Girona
19: Granada
20: Guadalajara
21: Huelva
22: Huesca
23: Jaen
24: Leon
25: Lleida
26: Logrono
27: Lugo
28: Madrid
29: Malaga
30: Melilla
31: Merida
32: Murcia
33: Ourense
34: Oviedo
35: Palencia
36: Palma
37: Pamplona
38: Pontevedra
39: Salamanca
40: Santander
41: Santiagodecompostela
42: Segovia
43: Sevilla
44: Soria
45: Tarragona
46: Teruel
47: Toledo
48: Valencia
49: Valladolid
50: Vitoria
51: Zamora
52: Zaragoza

Seleccione el número de la ciudad: 52

Usted ha seleccionado Zaragoza
['https://www.airbnb.es/s/Zaragoza-Spain/homes?refinement_paths%5B%5D=%2Fhomes']

Vamos a proceder al escrapeo de los alojamientos encontrados, por favor, espere a que termine el proceso.


SessionNotCreatedException: Message: session not created: probably user data directory is already in use, please specify a unique value for --user-data-dir argument, or don't use --user-data-dir
Stacktrace:
#0 0x58a2f60c57ca <unknown>
#1 0x58a2f5bbd2f0 <unknown>
#2 0x58a2f5bf4063 <unknown>
#3 0x58a2f5bf08c6 <unknown>
#4 0x58a2f5c3dbc9 <unknown>
#5 0x58a2f5c3d216 <unknown>
#6 0x58a2f5c31753 <unknown>
#7 0x58a2f5bfebaa <unknown>
#8 0x58a2f5bffdfe <unknown>
#9 0x58a2f609038b <unknown>
#10 0x58a2f6094307 <unknown>
#11 0x58a2f607ce7c <unknown>
#12 0x58a2f6094ec7 <unknown>
#13 0x58a2f606124f <unknown>
#14 0x58a2f60b42f8 <unknown>
#15 0x58a2f60b44c0 <unknown>
#16 0x58a2f60c4646 <unknown>
#17 0x7fe752032ac3 <unknown>


####2.2 Df_Temporal y df_ANUNCIOS


Con la información obtenida previamente a partir del listado de alojamientos disponibles, lo que hacemos es crear un Dataframe, llamado df_Temporal. Una vez generado lo modificamos, eliminando aquellos anuncios repetidos, lo cual sabemos gracias a la URL recién conseguida en este paso. La información obtenida la guardamos en un archivo CSV.

Este listado de información, limpia y sin registros duplicados, se almacena en un nuevo dataframe, df_ANUNCIOS. En este, iremos recopilando todos los anuncios nuevos que vayamos obteniendo cada vez que ejecutemos el punto 2.1 anterior y que no estén ya almacenados en él.

En cada iteración del punto 2.1, para introducir en df_ANUNCIOS los nuevos registros obtenidos y que en dicho momento están almacenados en df_temporal, se hace uso de un tercer df, df_base_limpio, el cual me guardará únicamente los registros que no estén almacenados ya en df_ANUNCIOS.

Concatenando ambos, conseguiré ampliar el listado de registros de df_ANUNCIOS.

Por motivos de seguridad, en todos los df que vamos generando en este paso, anteriores y posteriores, generaremos sus respectivos archivos csv para tener una recopilacion local de la información obtenida hasta el momento.


In [ ]:
df_Temporal = pd.DataFrame({
    'Título': titulos,
    'Título2': titulos2,
    'Precio por noche': precios,
    'Calificación': rating,
    'ID': apartment_id,
    "Ciudad": ciudad})


# Eliminamos \n del campo Calificación
df_Temporal['Calificación'] = df_Temporal['Calificación'].str.replace('\n', ' ', regex=False)
# Creamos la URL de cada anuncio a partir del apartament_id
df_Temporal['URL'] = "https://www.airbnb.es/rooms/" + df_Temporal['ID'].astype(str)
# Eliminar duplicados basados solo en ciertas columnas
df_Temporal = df_Temporal.drop_duplicates(subset=['URL'])
print(f"Para la última iteración, tenemos un df_Temporal con longitud: {len(df_Temporal['Título'])}")
df_Temporal.to_csv('/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/01.Temporales/df_Temporal.csv', index=False)


# Cargamos o creamos df_ANUNCIOS
try:
    df_ANUNCIOS = pd.read_csv('/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/df_ANUNCIOS.csv')
    print(f"\nAntes de la extracción, df_ANUNCIOS cuenta con una longitud de: {len(df_ANUNCIOS['Título'])}")
    # Agrupar por la columna 'Ciudad' del df_ANUNCIOS y contar las ocurrencias
    ciudades_agrupadas = df_ANUNCIOS.groupby('Ciudad').size()
    print(ciudades_agrupadas)
except:
    df_ANUNCIOS = pd.DataFrame({
        'Título': (),
        'Título2': (),
        'Precio por noche': (),
        'Calificación': (),
        'ID': (),
        "Ciudad": (),
        "URL": ()    })

# Filtrar y eliminar las filas de df_Temporal que están en df_ANUNCIOS
df_base_limpio = df_Temporal[~df_Temporal['URL'].isin(df_ANUNCIOS['URL'])]
print(f"\nHemos encontrado {len(df_base_limpio['Título'])} anuncios nuevos, almancenados en df_base_limpio y añadidos a df_ANUNCIOS")

# Añadimos datos nuevos y guardamos
df_ANUNCIOS = pd.concat([df_ANUNCIOS, df_base_limpio], ignore_index=True)
df_ANUNCIOS.to_csv('/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/df_ANUNCIOS.csv', index=False)

GUARDADO_SEGURIDAD=f'/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/00.Copias de seguridad/df_ANUNCIOS_{datetime.now()}.csv'
df_ANUNCIOS.to_csv(GUARDADO_SEGURIDAD, index=False)

ciudades_agrupadas = df_ANUNCIOS.groupby('Ciudad').size()
print(f"\nDespués de añadir estos anuncios no recopilados previamente, df_ANUNCIOS cuenta con una longitud de: {len(df_ANUNCIOS['Título'])}")
print(ciudades_agrupadas)


Para la última iteración, tenemos un df_Temporal con longitud: 306

Antes de la extracción, df_ANUNCIOS cuenta con una longitud de: 6436
Ciudad
Barcelona          1123
Bilbao              335
Huelva              277
Logrono             327
Madrid              925
Malaga              341
Málaga              273
Pamplona            306
Sevilla             718
Valencia            847
Valladolid          306
Vitoria-gasteiz     306
Zaragoza            352
dtype: int64

Hemos encontrado 0 anuncios nuevos, almancenados en df_base_limpio y añadidos a df_ANUNCIOS

Después de añadir estos anuncios no recopilados previamente, df_ANUNCIOS cuenta con una longitud de: 6436
Ciudad
Barcelona          1123
Bilbao              335
Huelva              277
Logrono             327
Madrid              925
Malaga              341
Málaga              273
Pamplona            306
Sevilla             718
Valencia            847
Valladolid          306
Vitoria-gasteiz     306
Zaragoza            352
dtype: int64

####2.3 Pendiente de escrapear


Una vez tenemos el listado de alojamientos que debemos escrapear debemos tener en cuenta una serie de puntos antes de proceder con el escrapeo individualizado de cada uno, correspondiente al siguiente punto 2.4.

En la primera ejecución de código de este punto no hay ningun anuncio cuya información se haya escrapeado completamente y añadido toda ella a un df definitivo (el cual llamaremos df_AIRBNB).

Pero, a partir de la segunda, yo ya puedo ver si del anuncio/s que quiero escrapear, almacenado en df_ANUNCIOS, he conseguido sacar toda su info y ha quedado almacenado en df_AIRBNB. Esto es muy importante tenerlo en cuenta ya que debo evitar volver a escrapear individualmente un anuncio que ya ha sido almacenado, con los costes de tiempo que implica.

Por lo tanto, defino un df, llamado df_pendientes, que sera el dataframe que albergará a todos los anuncios que faltan por iterar individualmente en el punto 2.4. En la primera iteración, como no existe aún el df definitivo (df_AIRBNB), iterará tomando todos los anuncios que estén en df_Anuncios; mientras, en el resto de iteraciones, solo en aquellos que No estén en el df definitivo (df_AIRBNB): bien porque se han añadido nuevos tras ejecutar de nuevo los punto 2.1 y 2.2, bien por que hemos parado el proceso de escrapeo 2.4. voluntariamente o incluso porque se haya producido algún error durante la ejecución del mismo, como un rechazo de conexión, falta de datos encontrados...

Respecto a esto último, nos permitirá hacer frente a aquellos escrapeos en los que no ha sido posible obtener la información completa definida en el punto 2.4., para volver a reintentarlo en posteriores ejecuciones del código.

Se ha añadido un punto en el cual, aquellos anuncios que en el momento de escrapeo hayan sido eliminados, no se tengan en cuenta entre los pendientes.


In [ ]:
try:
    # Intenta leer el archivo final de almacenamiento de los datos escrapeados
    df_AIRBNB = pd.read_csv('/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/df_AIRBNB.csv')
    # Carga de listado de anuncios almacenados
    df_ANUNCIOS = pd.read_csv('/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/df_ANUNCIOS.csv')
    # Obtención de los anuncios que faltan por escrapear individulamente en el siguiente apartado.
    df_pendientes= df_ANUNCIOS[~df_ANUNCIOS['URL'].isin(df_AIRBNB['URL'])]
    #Pendientes por ciudad
    ciudades_agrupadas = df_pendientes.groupby('Ciudad').size()
    print(ciudades_agrupadas)

    print(f"Hay un total de {len(df_pendientes['URL'])} anuncios pendientes de escrapear")


except:
    # Carga del listado de anuncios registrados. Esta línea de código sirve para la primera iteración del punto 2.4
    # donde aún no tengo creado el df definitivo df_AIRBNB al no haber escrapeado individualmente nada.
    df_ANUNCIOS = pd.read_csv('/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/df_ANUNCIOS.csv')
    df_pendientes = df_ANUNCIOS
    print(f"Es la primera iteración, todos los anuncios están pendientes de escrapear")

# Guardado pendientes
df_pendientes.to_csv('/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/df_pendientes.csv', index=False)


#URLs que entorpecen el escrapeo por tener puntos no definidos en el escrapeo por anuncio individual, opcional
blacklist = [
             ]
# Borrado de blacklist
df_pendientes = df_pendientes[~df_pendientes['URL'].isin(blacklist)]

####2.4 Escrapeado por anuncio individual


En este punto se procede a escrapear individualmente cada uno de los anuncios de los que está pendiente extraer toda su información, véase, aquellos almacenados en df_pendientes. Por medio de la URL, y haciendo uso de las librerías de escrapeo: Beautiful Soup y Selenium, iremos recogiendo toda la información valiosa y la almacenaremos en un diccionario.  

Se extrae información relativa al nombre y descripción del alojamiento, ratings, servicios, huéspedes, camas, habitaciones y ubicacion del mismo.

Para evitar que el código se rompa: por rechazo de conexión, falta de información en algún anuncio, o directamente porque decidimos parar la ejecución, se ha programdo de tal forma que cada 20 anuncios se genera un dataframe parcial, df_parcial, el cual será único cada vez que se crea, evitando así que se sobreescriba. En él, eliminamos cualquier registro que contenga algún nulo.

En caso de que algún anuncio nos este dando problemas, por ejemplo, porque ya no aparece, podemos al final de este punto incluirlo en la lista 'blacklist' mencionada anteriormente en el punto 2.3. En este caso, ejecutando el código quitaremos del listado de anuncios df_ANUNCIOS el mismo, para que no se tenga más en cuenta.

In [ ]:
# Creación de diccionario con listas vacías, donde se almacenarán
# los datos escrapeados de cada anuncio, encontrados en su URL correspondiente

dict_BASE = {
                'URL':[],
                'Nombre Alojamiento':[],
                'Descripcion':[],
                'Latitud':[],
                'Longitud':[],
                'Rating Limpieza':[],
                'Rating Veracidad':[],
                'Rating Llegada':[],
                'Rating Comunicacion':[],
                'Rating Ubicacion':[],
                'Rating Calidad':[],
                "Servicios":[],
                "accommodates":[],
                "bathrooms":[],
                "bedrooms":[],
                "beds":[],
                "Fecha registro":[]
                }

In [ ]:
print("Iniciando...")

ua = UserAgent()
chrome_options.add_argument(f'user-agent={ua.random}')
driver = webdriver.Chrome(options=chrome_options)

ruta_guardado = '/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/01.Temporales'
contador_url = 1
lista_tiempos=[]

prueba=["https://www.airbnb.es/rooms/51447836"]

# for url in df_pendientes['URL']:
# for url in reversed(df_pendientes['URL'].tolist()):
for url in df_pendientes['URL'].iloc[1000:]:

# for url in prueba:

    start_time = time.time()

    dict_BASE['URL'].append(url)
    driver.get(url)

    # Scroll hasta el final de la página para cargar todo el contenido dinámico
    driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")
    time.sleep(2)
    # Espera explícita para asegurar que la página ha cargado en lugar de usar sleep
    WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.TAG_NAME, 'body')))

    pendientes = len(df_pendientes['URL'])-contador_url
    print(f"\nVamos a por la URL número {contador_url} de {len(df_pendientes['URL'])}:")
    print(url)


    # Obtener el HTML de la página
    html = driver.page_source
    soup = bs(html, 'html.parser')

# ---------------------------------------------------------------------------------------------------------------------------------
# ---------------------------------------------------------------------------------------------------------------------------------
# ----Cerrar la traducción automática y cookies si salta el pop------------------------------------------------------------------------------
# ---------------------------------------------------------------------------------------------------------------------------------
    # Cerrar traductor
    cerrar_popups(driver)
    fecha_hora_actual = datetime.now()
    mi_lista = []
    dict_BASE['Fecha registro'].append(fecha_hora_actual)

# ---------------------------------------------------------------------------------------------------------------------------------
# ---------------------------------------------------------------------------------------------------------------------------------
# --Descripcion-------------------------------------------------------------------------------------------------------
# ---------------------------------------------------------------------------------------------------------------------------------

    extraer_descripcion(driver, soup, dict_BASE)

# ---------------------------------------------------------------------------------------------------------------------------------
# ---------------------------------------------------------------------------------------------------------------------------------
# --Ratings-------------------------------------------------------------------------------------------------------
# ---------------------------------------------------------------------------------------------------------------------------------

    extraer_ratings(soup, dict_BASE)

# ---------------------------------------------------------------------------------------------------------------------------------
# ---------------------------------------------------------------------------------------------------------------------------------
# --Extracción de servicios-------------------------------------------------------------------------------------------------------
# ---------------------------------------------------------------------------------------------------------------------------------
    amenities_list = []
    amenities_set = set()

    # Espera a que el botón de "Mostrar los amenities" esté disponible y haz clic
    try:
        boton_amenities = WebDriverWait(driver, 10).until(EC.element_to_be_clickable((By.XPATH, "//button[starts-with(text(), 'Mostrar los')]")))
        boton_amenities.click()

        # Lista de selectores para los diferentes tipos de amenities
        amenities_selectors = [
            '[id*="pdp_v3_bathroom_"]',
            '[id*="pdp_v3_bedroom_laundry"]',
            '[id*="pdp_v3_entertainment"]',
            '[id*="pdp_v3_heating_cooling"]',
            '[id*="pdp_v3_internet_office"]',
            '[id*="pdp_v3_kitchen_dining"]',
            '[id*="pdp_v3_parking_facilities"]',
            '[id*="pdp_v3_services"]',
            '[id*="lock_on_all"]',
            '[id*="security_camera"]',
            '[id*="pdp_v3_home_safety"]'
        ]

        # Iteramos sobre cada selector y añadimos los resultados a la lista de amenities
        for selector in amenities_selectors:
            elementos_amenities = driver.find_elements(By.CSS_SELECTOR, selector)
            for elemento in elementos_amenities:
                amenities_list.append(elemento.text)

        # Limpiar y añadir los servicios únicos al conjunto
        for amenity in amenities_list:
            amenity = amenity.split('\n')[0]  # Si el texto tiene saltos de línea, solo tomamos el primero
            amenities_set.add(amenity)

        # Guardar los amenities extraídos en el diccionario
        print(f"Objetos encontrados: {amenities_set}")
        dict_BASE["Servicios"].append(amenities_set)

    except:
        print("No se pudo hacer clic en el botón de amenities: añadimos NULO")
        dict_BASE["Servicios"].append(None)

# ---------------------------------------------------------------------------------------------------------------------------------
# ---------------------------------------------------------------------------------------------------------------------------------
# --Extracción de Accommodates, Bathrooms, Bedrooms y Beds-------------------------------------------------------------------------------------------------------------------------------
# ---------------------------------------------------------------------------------------------------------------------------------
    accommodates = 0
    bathrooms = 0
    bedrooms = 0
    beds = 0
    Whererooms_list = []

    # Cargar el contenido de la página y crear el objeto soup
    html = driver.page_source
    soup = bs(html, 'html.parser')

    # Encontrar todos los elementos relevantes
    encontrado = soup.find_all('li', {'class': 'l7n4lsf atm_9s_1o8liyq_keqd55 dir dir-ltr'})

    # Mapeo de palabras clave a variables
    room_mapping = {
        'viajero': 'accommodates',
        'cama': 'beds',
        'baño': 'bathrooms',
        'dormitorio': 'bedrooms'}

    # Procesar cada elemento encontrado
    for item in encontrado:
        item_text = item.text.lower()

        for key, var in room_mapping.items():
            if key in item_text:
                num = re.search(r'\d+', item_text)
                value = int(num.group()) if num else 1  # Si se encuentra un número, úsalo, si no, usa 1

                # Incrementar la variable correspondiente
                if var == 'accommodates':
                    accommodates += value
                elif var == 'beds':
                    beds += value
                elif var == 'bathrooms':
                    bathrooms += value
                elif var == 'bedrooms':
                    bedrooms += value

        Whererooms_list.append(item.text)

    # Mostrar los resultados encontrados
    print(f"Encontradas {bathrooms} baños, {bedrooms} habitaciones y {beds} camas para {accommodates} viajeros")

    # Almacenar los resultados en el diccionario
    dict_BASE["accommodates"].append(accommodates)
    dict_BASE["bathrooms"].append(bathrooms)
    dict_BASE["bedrooms"].append(bedrooms)
    dict_BASE["beds"].append(beds)

    # Eliminar la lista temporal para liberar memoria
    del Whererooms_list

# ---------------------------------------------------------------------------------------------------------------------------------
# --Maps-------------------------------------------------------------------------------------------------------------
# ---------------------------------------------------------------------------------------------------------------------------------

    # Llamada a la función extraer_maps
    extraer_maps(driver, url, dict_BASE, pause_time=2)

# ---------------------------------------------------------------------------------------------------------------------------------

    # Estimaciones de tiempo de ejecución de código
    end_time = time.time()
    tiempo_anun = end_time - start_time
    lista_tiempos.append(tiempo_anun)
    promedio_tiempo=sum(lista_tiempos)/len(lista_tiempos)
    tiempo_previsto = (promedio_tiempo*pendientes)/60

    print(f" ")
    print(f"Tiempo de extracción de anuncio: {tiempo_anun:.2f} segundos")
    print(f"Quedan {pendientes} anuncios, tiempo restanta previsto: {conversor_horas(tiempo_previsto)} minutos ")
    print(f"----------------------------------------------")

    for value in dict_BASE.values():
        print(f"{len(value)}", end=", ")

    # Guardado parcial cada 20 iteraciones
    guardar_parcial(dict_BASE, contador_url)

    contador_url+=1
# ---------------------------------------------------------------------------------------------------------------------------------
# ---------------------------------------------------------------------------------------------------------------------------------
# ---------------------------------------------------------------------------------------------------------------------------------
# ---------------------------------------------------------------------------------------------------------------------------------

print(f"----------------------------------------------")
print(f"---------------\nAsí queda el diccionario: \n {dict_BASE}")

df_parcial = pd.DataFrame(dict_BASE)
df_parcial = df_parcial.dropna()
file_path = f"/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/01.Temporales/df_parcial_{len(df_parcial)}_{datetime.now()}.csv"
df_parcial.to_csv(file_path, index=False)
print(f"\nGuardado parcial tras finalizar.\n")



In [ ]:
try:
    df_ANUNCIOS = pd.read_csv('/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/df_ANUNCIOS.csv')

    eliminar_manual=""
    blacklist.append(eliminar_manual)

    df_ANUNCIOS = df_ANUNCIOS[~df_ANUNCIOS['URL'].isin(blacklist)]
    df_ANUNCIOS.to_csv('/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/df_ANUNCIOS.csv', index=False)
    print(f"Borrados de df_ANUNCIOS: {blacklist}")
except:
    print("No borramos nada")


####2.5 Comprobación de resultados y unificación de DF

En el punto anterior, hemos ido generando df parciales, los cuales a continuación pasamos a cargar en un único df, de nombre df_ANUNCIOS_temporal. A estos, le añadiremos los últimos registros escrapeados que por no llegar a 20, no han podido guardarse.

El siguiente paso es borrar los posibles duplicados, definiendo así el df_AIRBNB_temporal. Para a continuacion, añadirle la información inicial obtenida al sacar el listado de alojamientos, el df_ANUNCIOS. Por lo tanto, con un INNER JOIN, redefinimos el df_AIRBNB_temporal el cual ya tiene toda la información del anuncio.

Por último, el df definitivo será el df_AIRBNB, el cual, tras crearse por primera a partir del df_AIRBNB_temporal, se irá el resto de ejecuciones de código alimentadose de toda la información que se le va añadiendo fruto de escrapear en el punto 2.4 y recopilarlo en este mismo 2.5. El borrar duplicados nos garantiza que el df final no presenta ningún anuncio repetido.

In [ ]:
# Ruta de guardado, la repetimos porque la hemos necesito cuando hemos querido guardar esta casilla de forma individual
ruta_guardado = '/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/01.Temporales'
# Al finalizar todas las iteraciones, cargo archivos parciales y consolido todo
df_ANUNCIOS_temporal = cargar_archivos_parciales(ruta_guardado)

# Añado los datos del último escrapeo temporal:
# df_último = pd.DataFrame(dict_BASE)
# Y lo junto con lo que he ido guardando cada 20:
# df_ANUNCIOS_temporal = pd.concat([df_ANUNCIOS_temporal, df_último], ignore_index=True)
df_ANUNCIOS_temporal = df_ANUNCIOS_temporal.drop_duplicates(subset=['URL'])

# Guardo el csv en drive
file_path = '/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/01.Temporales/df_ANUNCIOS_temporal.csv'
df_ANUNCIOS_temporal.to_csv(file_path, index=False)
print(f"Registros encontrados: {len(df_ANUNCIOS_temporal['Nombre Alojamiento'])}")


# Ahora, con los datos obtenidos en el df_ANUNCIOS_temporal, fruto de escrapear
# las URLs conseguidas en df_anuncios, y este último, hago un inner para juntar ambas tablas en una sola, con toda la info:
# la sacada en el listado de pags y la de entrar dentro del propio anuncio.
df_AIRBNB_temporal = df_ANUNCIOS_temporal.dropna()
df_AIRBNB_temporal = pd.merge(df_AIRBNB_temporal, df_ANUNCIOS, on='URL', how='inner')
file_path = "/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/01.Temporales/df_AIRBNB_temporal.csv"
df_AIRBNB_temporal.to_csv(file_path, index=False)
print(f"Registros df_AIRBNB_temporal: {len(df_AIRBNB_temporal['Nombre Alojamiento'])}")


# Obtención del df final, df_AIRBNB. La primera vez que se cree, será a través del except, pues no existe.
try:
    df_AIRBNB = pd.read_csv('/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/df_AIRBNB.csv')
    df_AIRBNB=pd.concat([df_AIRBNB, df_AIRBNB_temporal], ignore_index=True)
    df_AIRBNB=df_AIRBNB.drop_duplicates(subset=['URL'])
    print(f"Recargamos, Registros df_AIRBNB: {len(df_AIRBNB['Nombre Alojamiento'])}")
    df_AIRBNB.to_csv('/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/df_AIRBNB.csv', index=False)

    GUARDADO_SEGURIDAD=f'/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/00.Copias de seguridad/df_AIRBNB_{datetime.now()}.csv'
    df_AIRBNB.to_csv(GUARDADO_SEGURIDAD, index=False)

except:
    df_AIRBNB = df_AIRBNB_temporal
    file_path = '/content/drive/MyDrive/Compartidos/df_AIRBNB.csv'
    df_AIRBNB.to_csv(file_path, index=False)
    print(f"Creado, Registros df_AIRBNB: {len(df_AIRBNB['Nombre Alojamiento'])}")


###3- Limpieza y Transformación de datos

#### 3.0 Carga de csv

In [2]:
# Cargo df de lectura y lo meto en una nueva variable para poder manipularlo tranquilamente
df_AIRBNB = pd.read_csv('/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/df_AIRBNB.csv')
df_limpieza = df_AIRBNB
# df_limpieza = df_AIRBNB[df_AIRBNB['Ciudad'].isin(['Madrid',"Barcelona","Valencia"])]
# Saco nombre y cantidad total de columnas
columnas_df = df_limpieza.columns.to_list()
columnas_df
print(f'Total de columnas: {len(columnas_df)}')

# Tipo de datos iniciales
df_limpieza.dtypes
print(f'Total de registros: {len(df_limpieza)}')

# tipo de las columnas
df_limpieza.dtypes

Total de columnas: 23
Total de registros: 7360


URL                     object
Nombre Alojamiento      object
Descripcion             object
Latitud                float64
Longitud               float64
Rating Limpieza         object
Rating Veracidad        object
Rating Llegada          object
Rating Comunicacion     object
Rating Ubicacion        object
Rating Calidad          object
Servicios               object
accommodates             int64
bathrooms                int64
bedrooms                 int64
beds                     int64
Fecha registro          object
Título                  object
Título2                 object
Precio por noche        object
Calificación            object
ID                       int64
Ciudad                  object
dtype: object

#### 3.1 Información General

In [ ]:
# Vamos columna por columna analizando los valores presentes, su tipología y aplicando los cambios cuando sea preciso
# Todo esto queda recogido en el excel 'Limpieza_df_AIRBNB', almacenado en DRIVE

#### URL ####
df_limpieza['URL']

#### Nombre Alojamiento ####
# Cambio nombre de la columna para que no tenga espacios
df_limpieza.rename(columns={'Nombre Alojamiento': 'Nombre_Alojamiento'}, inplace=True)
df_limpieza['Nombre_Alojamiento']

#### Descripción ####
# Reemplazo de valores que indican 'Parte de la información se ha traducido automáticamente.' por 'Sin descripción'.
df_limpieza.loc[df_limpieza['Descripcion'] == 'Parte de la información se ha traducido automáticamente.', 'Descripcion'] = 'Sin Descripcion'
df_limpieza['Descripcion']

#### Titulo ####
df_limpieza['Título']
df_limpieza['Título'].value_counts()

#### Titulo 2 ####
# Se corresponde con la columna nombre alojamiento, y por lo tanto, la borramos.
df_limpieza.drop(columns=['Título2'], inplace=True)

#### ID ####
df_limpieza['ID']
df_limpieza['ID'].value_counts()

#### Ciudad ####
df_limpieza['Ciudad']
df_limpieza['Ciudad'].value_counts()

#### Precio por noche ####
# Primero renombro a un título sin espacios
df_limpieza.rename(columns={'Precio por noche':'Precio_noche'}, inplace=True)

# Quitamos el símbolo del euro, que viene con el espacio y cambio a tipo entero
df_limpieza['Precio_noche']=df_limpieza['Precio_noche'].str.replace(' € ','').str.replace('.', '').astype('int64')

#### Latitud y Longitud ####
df_limpieza[['Latitud','Longitud']]

#### Fecha Registro ####
df_limpieza['Fecha registro']
# Cambio el nombre a Fecha Scraping
df_limpieza.rename(columns={'Fecha registro': 'Fecha_Scraping'}, inplace=True)



#### 3.2. Ratings

In [ ]:
# Reemplazaremos los valores de los seis ratings en los que haya salido como valor:
# <div aria-hidden="true" class="r1lutz1s atm_c8_o7aogt atm_c8_l52nlx__oggzyc dir dir-ltr">Nuevo</div>
# sustituyéndolo simplemente por Nan. Esto pasa a nivel de anuncio, es decir, en el anuncio que nos encontramos
# este error se localiza en los 6 ratings a la vez
# Igualmente los convertimos en número

columnas_ratings = ['Rating Limpieza','Rating Veracidad','Rating Llegada','Rating Comunicacion','Rating Ubicacion','Rating Calidad']
for i in columnas_ratings:
    df_limpieza[i].replace('<div aria-hidden="true" class="r1lutz1s atm_c8_o7aogt atm_c8_l52nlx__oggzyc dir dir-ltr">Nuevo</div>',np.NaN,inplace=True)
    df_limpieza[i].replace('Nuevo',np.NaN,inplace=True)
    df_limpieza[i].replace(",",".",inplace=True)
    df_limpieza[i]=df_limpieza[i].astype('float64')

# Renombro los nombres para que no tengan espacios
df_limpieza.rename(columns={
    'Rating Limpieza':'Rating_Limpieza',
    'Rating Veracidad':'Rating_Veracidad',
    'Rating Llegada':'Rating_Llegada',
    'Rating Comunicacion':'Rating_Comunicacion',
    'Rating Ubicacion':'Rating_Ubicacion',
    'Rating Calidad':'Rating_Calidad'},inplace=True)


df_limpieza['Rating_Comunicacion'].value_counts()
# Compruebo que se ha convertido a tipo float64
print(df_limpieza['Rating_Comunicacion'].dtype)

float64


#### 3.3 Servicios

In [ ]:
### Vamos a crear un df que tenga los objetos únicos de Servicios

# Convertir las cadenas en listas (o conjuntos) reales
df_limpieza['Servicios'] = df_limpieza['Servicios'].apply(lambda x: ast.literal_eval(x))

# Cambiar cada elemento de la columna Servicios a lista
for i in range(len(df_limpieza['Servicios'])):
    df_limpieza['Servicios'][i] = list(df_limpieza['Servicios'][i])

# Cada elemento de cada lista de Servicios lo vamos a lower
for i in range(len(df_limpieza['Servicios'])):
    for j in range(len(df_limpieza['Servicios'][i])):
        df_limpieza['Servicios'][i][j] = df_limpieza['Servicios'][i][j].lower()

# Asegurarse de que cada valor en la columna 'Servicios' sea una lista
# df_limpieza['Servicios'] = df_limpieza['Servicios'].apply(lambda x: x if isinstance(x, list) else [x])

# Combinar todas las listas o conjuntos de servicios en una sola lista
todos_los_servicios = df_limpieza['Servicios'].explode().tolist()

# Obtener los servicios únicos
servicios_unicos = list(set(todos_los_servicios))

# Crear un nuevo DataFrame con una columna llamada 'df_servicios_únicos'
df_servicios_unicos = pd.DataFrame(servicios_unicos, columns=['df_servicios_únicos'])
df_servicios_unicos.dropna(inplace=True)
# ordenamos alfabéticamente
df_servicios_unicos = df_servicios_unicos.sort_values(by='df_servicios_únicos')


# Guardamos en csv
df_servicios_unicos.to_csv('/content/drive/MyDrive/Compartidos/df_servicios_únicos.csv', index=False)
# Mostrar el DataFrame
print(df_servicios_unicos)


# Ver el tipo de datos de la columna 'Servicios'
df_limpieza['Servicios'].apply(lambda x: type(x))

for i in df_limpieza['Servicios']:
    i

                          df_servicios_únicos
0                                            
331                            acondicionador
1036                  acondicionador de blanc
379                  acondicionador de básico
342   acondicionador de champu-gel- ecológico
...                                       ...
1073                   wifi rápido (929 mbps)
322                     wifi rápido (94 mbps)
1434                    wifi rápido (95 mbps)
1421                    wifi rápido (96 mbps)
944                        zona para trabajar

[1890 rows x 1 columns]


In [ ]:
# Vamos a crear columnas nuevas relativas a servicios específicos que pueden ser de interés
# a la hora de decidirnos por un alojamiento, en base a palabras clave
patrones_playa = ["playa", "beach", "paseo maritimo"]

### Cercanía a la playa
df_limpieza['Serv_playa'] = 0
df_limpieza['Serv_playa'] = df_limpieza.apply(
    lambda row: 1 if any(
        palabra.lower() in str(row['Nombre_Alojamiento']).lower() or
        palabra.lower() in str(row['Título']).lower() or
        palabra.lower() in str(row['Descripcion']).lower() or
        any(palabra.lower() in str(servicio).lower() for servicio in row['Servicios'])
        for palabra in patrones_playa
    ) else 0,
    axis=1)

### Disponibilidad de aparcamiento
patrones_parking = ["aparcamiento"]

df_limpieza['Serv_parking'] = 0
df_limpieza['Serv_parking'] = df_limpieza.apply(
    lambda row: 1 if any(
        palabra.lower() in str(row['Nombre_Alojamiento']).lower() or
        palabra.lower() in str(row['Título']).lower() or
        palabra.lower() in str(row['Descripcion']).lower() or
        any(palabra.lower() in str(servicio).lower() for servicio in row['Servicios'] if isinstance(row['Servicios'], list))
        for palabra in patrones_parking
    ) else 0,
    axis=1)

### Disponibilidad de conexión WIFI
patrones_internet = ["wifi", "internet"]

df_limpieza['Serv_internet'] = 0
df_limpieza['Serv_internet'] = df_limpieza.apply(
    lambda row: 1 if any(
        palabra.lower() in str(row['Nombre_Alojamiento']).lower() or
        palabra.lower() in str(row['Título']).lower() or
        palabra.lower() in str(row['Descripcion']).lower() or
        any(palabra.lower() in str(servicio).lower() for servicio in row['Servicios'] if isinstance(row['Servicios'], list))
        for palabra in patrones_internet
    ) else 0,
    axis=1)

### Disponibilidad de piscina
patrones_piscina = ["piscina", "pool"]

df_limpieza['Serv_piscina'] = 0
df_limpieza['Serv_piscina'] = df_limpieza.apply(
    lambda row: 1 if any(
        palabra.lower() in str(row['Nombre_Alojamiento']).lower() or
        palabra.lower() in str(row['Título']).lower() or
        palabra.lower() in str(row['Descripcion']).lower() or
        any(palabra.lower() in str(servicio).lower() for servicio in row['Servicios'] if isinstance(row['Servicios'], list))
        for palabra in patrones_piscina
    ) else 0,
    axis=1)


df_limpieza.columns

Index(['URL', 'Nombre_Alojamiento', 'Descripcion', 'Latitud', 'Longitud',
       'Rating_Limpieza', 'Rating_Veracidad', 'Rating_Llegada',
       'Rating_Comunicacion', 'Rating_Ubicacion', 'Rating_Calidad',
       'Servicios', 'accommodates', 'bathrooms', 'bedrooms', 'beds',
       'Fecha_Scraping', 'Título', 'Precio_noche', 'Calificación', 'ID',
       'Ciudad', 'Serv_playa', 'Serv_parking', 'Serv_internet',
       'Serv_piscina'],
      dtype='object')

#### 3.4 Tipología de Alojamiento

In [ ]:
# Extracción de títulos a otro df, quitamos duplicados y ordenamos
todos_los_titulos = df_limpieza['Título'].tolist()
df_titulos = pd.DataFrame(todos_los_titulos, columns=['df_titulos'])
# df_titulos = df_titulos.drop_duplicates()
df_titulos = df_titulos.sort_values(by='df_titulos')

# Guardamos en csv
df_titulos.to_csv('/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/df_titulos_únicos.csv', index=False)

# Mostrar el DataFrame
print(df_titulos)
len(df_titulos)
df_titulos.value_counts()


                          df_titulos
3939         Adosado en Arrigorriaga
2716  Adosado en Cabezón de Pisuerga
5889      Adosado en Cartaya, España
6139    Adosado en Centro de Córdoba
846                Adosado en Cihuri
...                              ...
459                              NaN
460                              NaN
461                              NaN
462                              NaN
1648                             NaN

[6745 rows x 1 columns]


df_titulos                                               
Apartamento en València                                      394
Habitación en Barcelona                                      369
Apartamento en Barcelona                                     291
Apartamento en Sevilla                                       245
Apartamento en Logroño                                       233
                                                            ... 
Casa de invitados en Vila Real de Santo António, Portugal      1
Casa de invitados en Vitoria-Gasteiz                           1
Casa de invitados en Zaragoza                                  1
Casa del árbol en Anguciana                                    1
Yurta en Barcelona                                             1
Name: count, Length: 926, dtype: int64

In [ ]:
# Vamos a crear una columna adjunta en la cual en base a la presencia o no de 'palabras clave' definiremos el tipo de alojamiento (habitación,
# vivienda, apartamento, cama, etc)

patrones_alojamiento = {
    "Adosado": "Casa entera",
    "Alojamiento": "Alojamiento",
    "Apartahotel": "Apartahotel",
    "Apartamento": "Apartamento",
    "Apto": "Apartamento",
    "Barco": "Casa entera",
    "Bed and breakfast": "Habitación",
    "Bungalow": "Bungalow",
    "Cabaña": "Casa entera",
    "Caravana": "Casa entera",
    "Casa de invitados": "Casa entera",
    "Casa particular": "Casa entera",
    "Casa rural": "Casa entera",
    "Cueva": "Casa entera",
    "Habitación Compartida": "Habitación Compartida",
    "Habitación": "Habitación",
    "Hostal": "Hostal",
    "Hotel boutique": "Hotel boutique",
    "Hotel": "Hotel",
    "Loft": "Loft",
    "Minicasa": "Casa entera",
    "Suite": "Suite",
    "Villa": "Casa entera",
    "Vivienda vacacional":"Vivienda vacacional",
    "Vivienda": "Vivienda",
    "Yurta": "Casa entera"
}
df_limpieza['Título'] = df_limpieza['Título'].fillna('')
for palabra_clave, tipo_alojamiento in patrones_alojamiento.items():
  df_limpieza.loc[df_limpieza['Título'].str.contains(palabra_clave, case=False, regex=False, na=None), 'Tipo_alojamiento'] = tipo_alojamiento
#Busco los registros que tienen como nulo el campo tipo alojamiento
df_limpieza[df_limpieza['Tipo_alojamiento'].isnull()]
# Comprobación de resultados
df_limpieza[['Título','Tipo_alojamiento']]
df_limpieza['Tipo_alojamiento'].value_counts()



Tipo_alojamiento
Apartamento    3512
Habitación     1861
Casa entera     581
Loft            261
Vivienda        243
Alojamiento     113
Hotel            69
Hostal           35
Suite            34
Bungalow          4
Name: count, dtype: int64

In [ ]:
df_limpieza.columns

Index(['URL', 'Nombre_Alojamiento', 'Descripcion', 'Latitud', 'Longitud',
       'Rating_Limpieza', 'Rating_Veracidad', 'Rating_Llegada',
       'Rating_Comunicacion', 'Rating_Ubicacion', 'Rating_Calidad',
       'Servicios', 'accommodates', 'bathrooms', 'bedrooms', 'beds',
       'Fecha_Scraping', 'Título', 'Precio_noche', 'Calificación', 'ID',
       'Ciudad', 'Serv_playa', 'Serv_parking', 'Serv_internet', 'Serv_piscina',
       'Tipo_alojamiento'],
      dtype='object')

In [ ]:
# Vamos a crear una segunda columna adjunta en la cual realizaremos lo mismo que en el paso anterior, pero esta vez
# categorizándolo por menos opciones.

patrones_alojamiento = {
    "Adosado": "Entire home/apt",
    "Alojamiento": "Private room",
    "Apartahotel": "Hotel room",
    "Apartamento": "Entire home/apt",
    "Apto": "Entire home/apt",
    "Barco": "Entire home/apt",
    "Bed and breakfast": "Private room",
    "Bungalow": "Entire home/apt",
    "Cabaña": "Entire home/apt",
    "Caravana": "Entire home/apt",
    "Casa de invitados": "Entire home/apt",
    "Casa particular": "Entire home/apt",
    "Casa rural": "Entire home/apt",
    "Cueva": "Entire home/apt",
    "Habitación": "Private room",
    "Habitación Compartida": "Shared room",
    "Hostal": "Hotel room",
    "Hotel": "Hotel room",
    "Hotel boutique": "Hotel room",
    "Loft": "Entire home/apt",
    "Minicasa": "Entire home/apt",
    "Suite": "Hotel room",
    "Villa": "Entire home/apt",
    "Vivienda vacacional":"Entire home/apt",
    "Vivienda": "Entire home/apt",
    "Yurta": "Entire home/apt"
}

for palabra_clave, tipo_alojamiento in patrones_alojamiento.items():
    df_limpieza.loc[df_limpieza['Título'].str.contains(palabra_clave, case=False, regex=False, na=None), 'Tipo_alojamiento_agrupado'] = tipo_alojamiento
#Busco los registros que tienen como nulo el campo tipo alojamiento
df_limpieza[df_limpieza['Tipo_alojamiento_agrupado'].isnull()]
# Comprobación de resultados
verfificacion = df_limpieza[['Título','Tipo_alojamiento_agrupado']]
verfificacion.to_csv('/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/verificacion.csv', index=False)
df_limpieza['Tipo_alojamiento_agrupado'].value_counts()



Tipo_alojamiento_agrupado
Entire home/apt    4601
Private room       1941
Hotel room          138
Shared room          33
Name: count, dtype: int64

#### 3.5 Estancias

In [ ]:
# Debido a que tras la extracción de datos encontramos registros en los que se obtiene 0 como valores, debemos realizar
# varias transformaciones para solventarlo en la medida de lo posible.
# Para ello, analizaremos distintos situaciones y plantearemos hipótesis para su resolucion, reduciendo de esta manera el nº de valores 0.

# Caso 1. Accommodates = 0, Bathrooms >= 1, Bedrooms = 0, Beds = 1.
# Situación que comprende un gran número de los registros en los que encontramos 0
# Si solo hay una cama, obviamente, estará en una habitación. La duda es que puede acomodar o bien a 1 o 2 personas.
# Nosotros consideramos la opción mínima y suponemos que alojará a 1 persona.

df_limpieza.loc[
    (df_limpieza['accommodates'] == 0) &
    (df_limpieza['bathrooms'] >= 1) &
    (df_limpieza['bedrooms'] == 0) &
    (df_limpieza['beds'] == 1),
    ['accommodates','bedrooms']] = [1,1]

df_limpieza['bathrooms'].value_counts()

# Caso 2. Bathrooms = 0
# Registros en los que solo tenemos 0 en la columna baños hay muy pocos, por lo tanto,
# los remplazamos por 1, ya que como mínimo habrá 1 y no es tan relevante el hecho de que haya 1 o más.
df_limpieza.loc[
    df_limpieza['bathrooms'] == 0,
    'bathrooms'] = 1

# Caso 3. Accommodates = 0, (Bathrooms >=1 (ya sucede en todos)), Bedrooms = 0, Beds > 1. Tipo alojamiento = habitacion
# En aquellos registros donde bedrooms es 0 y el tipo de alojamiento es habitación implicará que bedrooms = 1,
# reemplazaremos el accomodates = 0 con el valor correspondiente al número de camas.
# Igual que en el caso 1, tiraremos por lo mínimo (ya que cada cada podría albergar a 2 personas)

# Primero debo verificar que haya registros en los que se cumplen todas las consideraciones a la vez:
if (df_limpieza['accommodates'] == 0).any() and (df_limpieza['bedrooms']==0).any() \
   and (df_limpieza['beds']>1).any() and (df_limpieza['Tipo_alojamiento'] == 'Habitación').any():

   # Creo lo anterior como una condicion
   condicion_1 = (df_limpieza['accommodates'] == 0) & \
               (df_limpieza['bedrooms'] == 0) & \
               (df_limpieza['beds'] > 1) & \
               (df_limpieza['Tipo_alojamiento'] == 'Habitación')

   # Asigno valores de beds a accommodates
   df_limpieza.loc[condicion_1, 'accommodates'] = df_limpieza.loc[condicion_1, 'beds']

   # Asigno valores 1 a los bedrooms
   df_limpieza.loc[condicion_1, 'bedrooms'] = 1


# Caso 4. Accommodates > 0, Bedrooms = 0, Beds = 1.
# Aquellos casos en los que tenga nulo solo el nº de habitaciones, y haya 1 cama, el nº de habitaciones sera 1
if ((df_limpieza['accommodates']>0).any() and df_limpieza['bedrooms'] == 0).any()\
   and (df_limpieza['beds']==1).any():

   condicion_2 = (df_limpieza['accommodates'] > 0) & \
               (df_limpieza['bedrooms'] == 0) & \
               (df_limpieza['beds'] ==1)

   # Asigno valores de beds a bedrooms
   df_limpieza.loc[condicion_2, 'bedrooms'] = df_limpieza.loc[condicion_2, 'beds']


# Utilizar las siguientes líneas de código para detectar y analizar situaciones:
# Para saber cantidades:
# df_limpieza['accommodates'].value_counts()
# df_limpieza['bathrooms'].value_counts()
# df_limpieza['bedrooms'].value_counts()
# df_limpieza['beds'].value_counts()

# Para ver todas las posibles combinaciones:
# df_limpieza[['accommodates','bathrooms','bedrooms','beds']].value_counts()
# df_limpieza[['accommodates','bathrooms','bedrooms','beds']].loc[(df_limpieza['accommodates'] == 0) | (df_limpieza['beds'] == 0) | (df_limpieza['bedrooms'] == 0)]

# Usar esto para ir viendo las tablas de las combinaciones que desee:
# df_limpieza[['URL','Título','accommodates','bedrooms','beds']].loc[(df_limpieza['accommodates'] == 0) & (df_limpieza['beds'] == 0)& (df_limpieza['bedrooms'] == 0)]
# df_limpieza[['URL','Título','accommodates','bathrooms','bedrooms','beds']]

#### 3.6 Valoración media y nº Evaluaciones

In [ ]:
df_limpieza['Calificación']
df_limpieza['Calificación'].value_counts()

## Obtención de la valoración media

# Creamos una columna que se llamará valoracion media en la cual ya de primeras remplazamos el texto pertinente para los anuncios nuevos
# De esta forma, solo nos faltará manipularla para extraer los anuncios que si tienen valoración media.
df_limpieza['Valoración_media'] = df_limpieza['Calificación'].replace('Alojamiento nuevo Nuevo', np.NaN)

# Ahora manipulamos la columna para obtener los valores en los registros que tienen valoración media,
# serán por lo tanto aquellas que no tengan como valor el string 'Alojamiento Nuevo'.
# Para ello debo tener en cuenta que para poder hacer uso de los métodos de manipulación de strings, es preciso
# usar la función .str. Esto es aún más necesario dado que como la columna es de tipo object, en ellas no podré hacer
# uso de operacion de manipulación a menos que ponga delante la función str.
df_limpieza.loc[df_limpieza['Valoración_media'] != np.NaN, 'Valoración_media']=df_limpieza.loc[df_limpieza['Valoración_media'] != np.NaN, 'Valoración_media'].str.split('Valoración media de ').str[1].str.split(' sobre ').str[0]


### Cambio de formato a float64
df_limpieza['Valoración_media'] = df_limpieza['Valoración_media'].str.replace(',', '.')

df_limpieza['Valoración_media']=df_limpieza['Valoración_media'].astype('float64')

# Comprobación de formato
print(df_limpieza["Valoración_media"].dtype)
# recuento de nulos
df_limpieza['Valoración_media'].isnull().sum()


float64


521

In [ ]:
# Obtención del número de evaluaciones.

# Creo una columna nueva llamada nº de evaluaciones.
# Si en la columna de valoración media, tengo el texto 'Alojamiento Nuevo', pondré el texto Nulo
# En el resto de registros, como sí que hay valoración, se generan nulos en sí
df_limpieza.loc[df_limpieza['Valoración_media'].isnull(), 'Nº_evaluaciones'] = "Nulo"

# Obtengo el nº de evaluaciones en aquellos casos que existen, para ello reemplazamos los nulos con la cantidad de evaluaciones
df_limpieza.loc[df_limpieza['Nº_evaluaciones'] != "Nulo", 'Nº_evaluaciones']=df_limpieza.loc[df_limpieza['Calificación'] != 'Alojamiento nuevo Nuevo', 'Calificación'].str.split('(').str[1].str.split(')').str[0]

df_limpieza['Nº_evaluaciones'].isnull().sum()

# Cambio el tipo de dato a número entero (con el errors coerce, me cambia los strings "Nulos" a NaN)
print(df_limpieza['Nº_evaluaciones'].dtype)
df_limpieza['Nº_evaluaciones'] = pd.to_numeric(df_limpieza['Nº_evaluaciones'], errors='coerce').astype("Int64")
print(df_limpieza['Nº_evaluaciones'].dtype)

# Ahora podemos eliminar la columna calificación, ya que no nos sirve una vez extraida la info y añadida a estas dos nuevas columnas
df_limpieza.drop(columns=['Calificación'], inplace=True)


object
Int64


#### 3.7. Asociar latitudes y longitudes a distritos

##### Instalación de Bibliotecas y montaje de Google Drive

In [3]:
!pip install geopandas shapely pandas

# Geopandas y Shapely son herramientas clave para el análisis geoespacial y la manipulación de datos geoespaciales en Python
# Geopandas extiende la funcionalidad de pandas al proporcionar soporte para datos geoespaciales.
# Permite trabajar con datos espaciales tipo puntos, líneas, y polígonos, así como gestiona atributos no espaciales.

# Shapely crea, manipula y analiza objetos geométricos en Python. Geopandas la utiliza para gestionar geometrías espaciales.
# Permite crear geometrías, hacer mediciones espaciales (Longitudes, áreas), operaciones geométricas (union, intersección...)
# crear geometrías como puntos, líneas, polígonos...

In [4]:
import geopandas as gpd
import pandas as pd
from shapely.geometry import Point

##### Carga de los límites de los distritos

**Concepto de GeoDataframe**

Los límites de los distritos que utilizaremos se encuentran en distintos formatos de dato vectorial: tipo Geojson o bien tipo Shapefile.

Dichos archivos son cargados mediante la libreria Geopandas como un dato de tipo GeoDataframe, que es básicamente un DataFrame de Pandas pero además con una columna especial llamada geometry, que almacena objetos geométricos (puntos, líneas, polígonos, etc.) y permite realizar análisis espaciales. En nuestro caso particular, las columnas geometry albergarán los polígonos que representan los distritos de las distintas ciudades.

Geopandas es como una extensión del módulo Pandas, lo que significa que puedes usar la mayoría de las funcionalidades de Pandas en un GeoDataFrame. Además, añade nuevas funcionalidades específicas para trabajar con datos espaciales (como geometrías, operaciones espaciales, etc.).


**Definición del Sistema de Referencia de Coordenadas - CRS**

Debemos asegurarnos de que todos los datos de tipo espacial de los distintos archivos se encuentren en el mismo sistema de coordenadas (CRS), que es el que define como se representan las geometrías de la tierra.

En este caso particular, nos interesa que presenten el mismo: los archivos de delimitación de los distritos de cada una de las ciudades consideradas (la columna de geometría), y por otro lado, el archivo con los alojamientos escrapeados de AIRBNB (más concretamente sus columnas de latitud y longitud).

Cada CRS tiene un código EPSG (estándar numérico internacional). El 4326 es el estándar para latitud y longiutd en grados decimales.

*¿Por qué es importante usar el mismo CRS en todos los archivos?*

Los archivos geoespaciales pueden estar en diferentes sistemas de coordenadas:

*   Proyectados (como EPSG:25831, usado en España para UTM zona 31N).
*   Geográficos (como EPSG:4326, para coordenadas globales de latitud/longitud).

Si los CRS no coinciden:
*   Las geometrías no se alinearán correctamente en servicios de mapas. (Ya que muchos servicios de mapas, como google maps, usan este sistema 4326)
*   Los cálculos espaciales (distancias, áreas) serán incorrectos. (Ya que podría tener conjuntos de datos distintos con distinto CRS)

Nosotros buscaremos que todos los archivos se encuentren en el **EPSG:4326**.

Como los distintos archivos de distrito han sido obtenidos a partir de diferentes enlaces (principalmente los visores de datos autonómicos o municipales), debemos en cada carga de archivo comprobar el sistema CRS que tiene, pudiendo encontrarnos ante 3 situaciones posibles:
*   CRS sea por defecto, EPSG:4326. No hacemos nada en este caso, ya está bien
*   CRS sea otro distinto. Lo convertimos a EPSG: 4326
*   CRS No esté definido. Aquí es preciso informarse en la web de descarga del EPSG utilizado y definirlo, para posteriormente convertirlo a EPSG: 4326 si no es este.


Se ha creado la siguiente función para transformar el tipo de CRS según la hipótesis que se cumpla de las tres definidas en líneas anteriores:

In [5]:
def definicion_crs (archivo):

  # None en Python no se puede comparar directamente con números, pues representa la ausencia de valor o un valor nulo.
  # Comparar este con un número no es un error en sí, pero no tiene sentido lógico.
  # Por ello debo ponerlo primero de todo en un condicional en el que defina el CRS si no está definido (es decir, si es None)
  # Si ya está definido, pasará al segundo condicional en el que verifica si está en CRS 4326 o no, y en caso de darse el segundo
  # caso, se transforma al primero

  # CONDICIONAL 1. DEFINIMOS CRS SI ES NULO

  if archivo.crs is None:
    crs_origen = int(input("CRS no definido. Por favor, definir el CRS establecido en origen: "))
    archivo = archivo.set_crs(epsg =crs_origen)
    print(f"El CRS de origen es: {archivo.crs}")
    # añademe un salto de linea:
    print("\n")

  # CONDICIONAL 2. VERIFICAMOS SI CRS ES 4326, Y TRANSFORMAMOS SI NO ES EL CASO

  if archivo.crs == 4326:
    print(f"CRS correcto, {archivo.crs}")

  else:
    print(f"CRS incorrecto, {archivo.crs}, lo transformamos a EPSG: 4326")
    archivo = archivo.to_crs(epsg=4326)
    print(f"CRS actualizado, {archivo.crs}")

  return archivo  # Sin el return archivo, el archivo se actualizaría dentro de la función, pero una vez que la función termine,
                    # el archivo original fuera de la función no reflejaría estos cambios.

Dada la NO homogeneidad de los distintos archivos procedemos individualmente a cargarlos uno a uno, configurando tras ello al CRS mediante la función creada, y por último nos quedaremos con las columnas de geometría y distrito de entre todas las que presente el archivo, realizando si es preciso las transformaciones necesarias.

Entre ellas, una indispensable, renombrar la columna distrito para que una vez tengamos hecho todo lo comentando en todos los archivos, lo convirtamos en un único archivo.

Valencia

In [6]:
# Aumentamos al maximo el numero de columnas que se pueden mostrar por pantalla
pd.set_option('display.max_columns',None)

In [7]:
distritos_valencia = gpd.read_file('/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/02.Distritos/Contornos/Geojson/distritos_valencia.geojson')
distritos_valencia

# Configuro CRS
distritos_valencia = definicion_crs (distritos_valencia)

# Me quedo con la columna que alberga los distritos y la que alberga la geometría:
distritos_valencia = distritos_valencia[['nombre', 'geometry']]
# Renmobro columa 'nombre' a distrito:
distritos_valencia = distritos_valencia.rename(columns={'nombre': 'Distrito'})
# Transformo valores de Columna distrito, de todo mayúsculas a solo letra inicial:
distritos_valencia['Distrito'] = distritos_valencia['Distrito'].str.title()

# Modifico valores de los mismos, para que coincidan en procesos posteriores:
distritos_valencia.loc[distritos_valencia['Distrito'] == 'La Saidia', 'Distrito'] = 'La Saïdia'
distritos_valencia.loc[distritos_valencia['Distrito'] == 'Algiros', 'Distrito'] = 'Algirós'

# Creo columna llamada ciudad, con el nombre de la misma:
distritos_valencia['Ciudad'] = 'Valencia'

distritos_valencia

CRS correcto, EPSG:4326


Distrito                                           geometry  \
0    Poblats Del Nord  POLYGON ((-0.31988 39.56171, -0.31953 39.56214...   
1          Benimaclet  POLYGON ((-0.35489 39.47809, -0.36274 39.48389...   
2            Campanar  POLYGON ((-0.42651 39.495, -0.42612 39.49507, ...   
3    Poblats Maritims  POLYGON ((-0.33151 39.48561, -0.3315 39.48561,...   
4           La Saïdia  POLYGON ((-0.38947 39.48856, -0.38692 39.48916...   
5     El Pla Del Real  POLYGON ((-0.36229 39.48483, -0.36274 39.48389...   
6           Extramurs  POLYGON ((-0.3834 39.48116, -0.38302 39.48028,...   
7          L'Eixample  POLYGON ((-0.36454 39.47121, -0.36378 39.47024...   
8      Camins Al Grau  POLYGON ((-0.35441 39.47148, -0.34939 39.46996...   
9               Jesus  POLYGON ((-0.38801 39.46219, -0.38694 39.46267...   
10    Quatre Carreres  POLYGON ((-0.33584 39.44396, -0.33611 39.44076...   
11    Poblats Del Sud  POLYGON ((-0.41435 39.45959, -0.40921 39.45231...   
12            Patraix  POLYGON ((-0.41435 39.45959, -0.41434 39.45963...   
13   Poblats Del Nord  POLYGON ((-0.35509 39.52596, -0.3554 39.52535,...   
14       Ciutat Vella  POLYGON ((-0.38105 39.48223, -0.38023 39.48212...   
15            Algirós  POLYGON ((-0.34276 39.48706, -0.34266 39.48705...   
16           Rascanya  POLYGON ((-0.3677 39.50468, -0.3677 39.50457, ...   
17  Poblats De L'Oest  POLYGON ((-0.42651 39.495, -0.42653 39.49506, ...   
18        L'Olivereta  POLYGON ((-0.41293 39.46313, -0.41291 39.46316...   
19   Poblats Del Nord  POLYGON ((-0.4269 39.56233, -0.42669 39.56215,...   
20   Poblats Del Nord  POLYGON ((-0.32961 39.54649, -0.3296 39.54609,...   
21          Benicalap  POLYGON ((-0.39313 39.50433, -0.38889 39.50024...   

      Ciudad  
0   Valencia  
1   Valencia  
2   Valencia  
3   Valencia  
4   Valencia  
5   Valencia  
6   Valencia  
7   Valencia  
8   Valencia  
9   Valencia  
10  Valencia  
11  Valencia  
12  Valencia  
13  Valencia  
14  Valencia  
15  Valencia  
16  Valencia  
17  Valencia  
18  Valencia  
19  Valencia  
20  Valencia  
21  Valencia

Madrid

In [8]:
distritos_madrid = gpd.read_file('/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/02.Distritos/Contornos/Geojson/distritos_madrid.geojson')
distritos_madrid

# Configuro CRS
distritos_madrid = definicion_crs (distritos_madrid)

# Me quedo con la columna que alberga los distritos y la que alberga la geometría:
distritos_madrid = distritos_madrid[['name', 'geometry']]
# Renmobro columa 'nombre' a distrito:
distritos_madrid = distritos_madrid.rename(columns={'name': 'Distrito'})

# Modifico valores de los mismos, para que coincidan en procesos posteriores:
distritos_madrid.loc[distritos_madrid['Distrito'] == 'Chamartin', 'Distrito'] = 'Chamartín'
distritos_madrid.loc[distritos_madrid['Distrito'] == 'Tetuan', 'Distrito'] = 'Tetúan'
distritos_madrid.loc[distritos_madrid['Distrito'] == 'Chamberi', 'Distrito'] = 'Chamberí'
distritos_madrid.loc[distritos_madrid['Distrito'] == 'Vicalvaro', 'Distrito'] = 'Vicálvaro'
distritos_madrid.loc[distritos_madrid['Distrito'] == 'San Blas', 'Distrito'] = 'San Blas-Canillejas'

# Creo columna llamada ciudad, con el nombre de la misma:
distritos_madrid['Ciudad'] = 'Madrid'

distritos_madrid

CRS correcto, EPSG:4326


Distrito                                           geometry  \
0                Centro  MULTIPOLYGON (((-3.69185 40.40853, -3.69189 40...   
1            Arganzuela  MULTIPOLYGON (((-3.70258 40.40638, -3.70166 40...   
2                Retiro  MULTIPOLYGON (((-3.66279 40.4097, -3.66384 40....   
3             Salamanca  MULTIPOLYGON (((-3.65809 40.43945, -3.65828 40...   
4             Chamartín  MULTIPOLYGON (((-3.67231 40.48388, -3.67237 40...   
5                Tetúan  MULTIPOLYGON (((-3.69633 40.47572, -3.69619 40...   
6              Chamberí  MULTIPOLYGON (((-3.68991 40.44737, -3.69048 40...   
7   Fuencarral-El Pardo  MULTIPOLYGON (((-3.64131 40.63922, -3.64118 40...   
8       Moncloa-Aravaca  MULTIPOLYGON (((-3.79973 40.47063, -3.79887 40...   
9                Latina  MULTIPOLYGON (((-3.7213 40.41256, -3.72051 40....   
10          Carabanchel  MULTIPOLYGON (((-3.72346 40.40622, -3.72345 40...   
11                Usera  MULTIPOLYGON (((-3.6819 40.36592, -3.6819 40.3...   
12   Puente de Vallecas  MULTIPOLYGON (((-3.67705 40.3618, -3.67706 40....   
13            Moratalaz  MULTIPOLYGON (((-3.64158 40.41569, -3.63964 40...   
14        Ciudad Lineal  MULTIPOLYGON (((-3.62058 40.41671, -3.62031 40...   
15            Hortaleza  MULTIPOLYGON (((-3.65114 40.5123, -3.65095 40....   
16           Villaverde  MULTIPOLYGON (((-3.70235 40.36475, -3.70193 40...   
17    Villa de Vallecas  MULTIPOLYGON (((-3.60631 40.3882, -3.60524 40....   
18            Vicálvaro  MULTIPOLYGON (((-3.57633 40.41484, -3.57159 40...   
19  San Blas-Canillejas  MULTIPOLYGON (((-3.59198 40.45123, -3.59194 40...   
20              Barajas  MULTIPOLYGON (((-3.56045 40.51234, -3.56036 40...   

    Ciudad  
0   Madrid  
1   Madrid  
2   Madrid  
3   Madrid  
4   Madrid  
5   Madrid  
6   Madrid  
7   Madrid  
8   Madrid  
9   Madrid  
10  Madrid  
11  Madrid  
12  Madrid  
13  Madrid  
14  Madrid  
15  Madrid  
16  Madrid  
17  Madrid  
18  Madrid  
19  Madrid  
20  Madrid

Barcelona

In [9]:
distritos_barcelona = gpd.read_file('/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/02.Distritos/Contornos/Geojson/distritos_barcelona.geojson')
distritos_barcelona

# Configuro CRS
distritos_barcelona = definicion_crs (distritos_barcelona)

# Me quedo con la columna que alberga los distritos y la que alberga la geometría:
distritos_barcelona = distritos_barcelona[['NOM', 'geometry']]
# Renmobro columa 'nombre' a distrito:
distritos_barcelona = distritos_barcelona.rename(columns={'NOM': 'Distrito'})
# Creo columna llamada ciudad, con el nombre de la misma:
distritos_barcelona['Ciudad'] = 'Barcelona'

distritos_barcelona

CRS correcto, EPSG:4326


Distrito                                           geometry  \
0         Ciutat Vella  POLYGON ((2.18345 41.39061, 2.18459 41.38976, ...   
1             Eixample  POLYGON ((2.1869 41.40165, 2.18689 41.40087, 2...   
2       Sants-Montjuïc  MULTIPOLYGON (((2.14824 41.37623, 2.14896 41.3...   
3            Les Corts  POLYGON ((2.10342 41.4011, 2.10352 41.40109, 2...   
4  Sarrià-Sant Gervasi  MULTIPOLYGON (((2.07313 41.43522, 2.07319 41.4...   
5               Gràcia  POLYGON ((2.13629 41.42363, 2.1364 41.42358, 2...   
6       Horta-Guinardó  POLYGON ((2.15949 41.44977, 2.15942 41.4496, 2...   
7           Nou Barris  POLYGON ((2.18706 41.46772, 2.18711 41.46711, ...   
8          Sant Andreu  POLYGON ((2.18764 41.46212, 2.18765 41.46208, ...   
9           Sant Martí  POLYGON ((2.20736 41.42711, 2.20698 41.42665, ...   

      Ciudad  
0  Barcelona  
1  Barcelona  
2  Barcelona  
3  Barcelona  
4  Barcelona  
5  Barcelona  
6  Barcelona  
7  Barcelona  
8  Barcelona  
9  Barcelona

Sevilla

In [10]:
distritos_sevilla = gpd.read_file('/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/02.Distritos/Contornos/Geojson/distritos_sevilla.geojson')
distritos_sevilla

# Configuro CRS
distritos_sevilla = definicion_crs (distritos_sevilla)

# Me quedo con la columna que alberga los distritos y la que alberga la geometría:
distritos_sevilla = distritos_sevilla[['Distri_11D', 'geometry']]
# Renmobro columa 'nombre' a distrito:
distritos_sevilla = distritos_sevilla.rename(columns={'Distri_11D': 'Distrito'})

# Modifico valores de los mismos, para que coincidan en procesos posteriores:
distritos_sevilla.loc[distritos_sevilla['Distrito'] == 'San Pablo - Santa Justa', 'Distrito'] = 'San Pablo-Santa Justa'
distritos_sevilla.loc[distritos_sevilla['Distrito'] == 'Bellavista - La Palmera', 'Distrito'] = 'Bellavista-La Palmera'
distritos_sevilla.loc[distritos_sevilla['Distrito'] == 'Cerro - Amate', 'Distrito'] = 'Cerro-Amate'
distritos_sevilla.loc[distritos_sevilla['Distrito'] == 'Este - Alcosa - Torreblanca', 'Distrito'] = 'Este-Alcosa-Torreblanca'

# Creo columna llamada ciudad, con el nombre de la misma:
distritos_sevilla['Ciudad'] = 'Sevilla'

distritos_sevilla

CRS correcto, EPSG:4326


Distrito  \
0     San Pablo-Santa Justa   
1             Casco Antiguo   
2                   Nervión   
3                  Macarena   
4              Los Remedios   
5     Bellavista-La Palmera   
6                       Sur   
7               Cerro-Amate   
8   Este-Alcosa-Torreblanca   
9                    Triana   
10                    Norte   

                                             geometry   Ciudad  
0   POLYGON ((-5.98399 37.39307, -5.98382 37.39373...  Sevilla  
1   POLYGON ((-6.00654 37.39173, -6.00656 37.39244...  Sevilla  
2   POLYGON ((-5.98849 37.38115, -5.98815 37.38176...  Sevilla  
3   POLYGON ((-5.99729 37.40436, -5.99631 37.40532...  Sevilla  
4   MULTIPOLYGON (((-6.0315 37.30091, -6.03276 37....  Sevilla  
5   POLYGON ((-5.99045 37.36939, -5.99045 37.36926...  Sevilla  
6   POLYGON ((-5.9648 37.37048, -5.9625 37.36902, ...  Sevilla  
7   POLYGON ((-5.94076 37.38641, -5.94071 37.38641...  Sevilla  
8   POLYGON ((-5.87478 37.41237, -5.87477 37.41229...  Sevilla  
9   POLYGON ((-5.98885 37.41973, -5.98886 37.41864...  Sevilla  
10  POLYGON ((-5.94253 37.45193, -5.93508 37.44956...  Sevilla

Bilbao

In [11]:
distritos_bilbao = gpd.read_file('/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/02.Distritos/Contornos/Geojson/distritos_bilbao.geojson')
distritos_bilbao

# Configuro CRS
distritos_bilbao = definicion_crs (distritos_bilbao)

# Me quedo con la columna que alberga los distritos y la que alberga la geometría:
distritos_bilbao = distritos_bilbao[['distrito', 'geometry']]
# Renmobro columa 'nombre' a distrito:
distritos_bilbao = distritos_bilbao.rename(columns={'distrito': 'Distrito'})
# Creo columna llamada ciudad, con el nombre de la misma:
distritos_bilbao['Ciudad'] = 'Bilbao'

distritos_bilbao

CRS correcto, EPSG:4326


Distrito                                           geometry  Ciudad
0         7  MULTIPOLYGON (((-2.93493 43.24998, -2.93497 43...  Bilbao
1         3  MULTIPOLYGON (((-2.89696 43.25325, -2.89737 43...  Bilbao
2         2  MULTIPOLYGON (((-2.92276 43.2642, -2.92286 43....  Bilbao
3         4  MULTIPOLYGON (((-2.90586 43.24536, -2.90591 43...  Bilbao
4         5  MULTIPOLYGON (((-2.92161 43.25089, -2.92153 43...  Bilbao
5         6  MULTIPOLYGON (((-2.94063 43.2695, -2.93986 43....  Bilbao
6         8  MULTIPOLYGON (((-2.9505 43.25617, -2.95048 43....  Bilbao
7         1  MULTIPOLYGON (((-2.96794 43.28348, -2.96788 43...  Bilbao

In [12]:
# Debo convertir el número que identifica al distrito por su nombre (comprobado en cartografía):
# Lista con los nombres de los distritos
distritos_nombres = [
    "Recalde", "Ocharcoaga-Churdínaga", "Uribarri", "Begoña",
    "Ibaiondo", "Abando", "Basurtu-Zorrotza", "Deusto"
]

# Modificar los valores en la columna 'distrito' usando .loc[] por índice

for i, nombre in enumerate(distritos_nombres): # Enumerate devuelve el indice de la lista y el valor
    distritos_bilbao.loc[i, 'Distrito'] = nombre

distritos_bilbao

Distrito                                           geometry  \
0                Recalde  MULTIPOLYGON (((-2.93493 43.24998, -2.93497 43...   
1  Ocharcoaga-Churdínaga  MULTIPOLYGON (((-2.89696 43.25325, -2.89737 43...   
2               Uribarri  MULTIPOLYGON (((-2.92276 43.2642, -2.92286 43....   
3                 Begoña  MULTIPOLYGON (((-2.90586 43.24536, -2.90591 43...   
4               Ibaiondo  MULTIPOLYGON (((-2.92161 43.25089, -2.92153 43...   
5                 Abando  MULTIPOLYGON (((-2.94063 43.2695, -2.93986 43....   
6       Basurtu-Zorrotza  MULTIPOLYGON (((-2.9505 43.25617, -2.95048 43....   
7                 Deusto  MULTIPOLYGON (((-2.96794 43.28348, -2.96788 43...   

   Ciudad  
0  Bilbao  
1  Bilbao  
2  Bilbao  
3  Bilbao  
4  Bilbao  
5  Bilbao  
6  Bilbao  
7  Bilbao

Zaragoza

In [13]:
distritos_zaragoza = gpd.read_file('/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/02.Distritos/Contornos/Shapefile/zgz/distritos_zaragoza.shp')
print(distritos_zaragoza.crs)


# Configuro CRS
# CRS por defecto en descarga: 25830
distritos_zaragoza = definicion_crs (distritos_zaragoza)

# Me quedo con la columna que alberga los distritos y la que alberga la geometría:
distritos_zaragoza = distritos_zaragoza[['NOMBRE', 'geometry']]
# Renmobro columa 'nombre' a distrito:
distritos_zaragoza = distritos_zaragoza.rename(columns={'NOMBRE': 'Distrito'})

# Modifico valores de los mismos, para que coincidan en procesos posteriores:
distritos_zaragoza.loc[distritos_zaragoza['Distrito'] == 'Torrero - La Paz', 'Distrito'] = 'Torrero-La Paz'
distritos_zaragoza.loc[distritos_zaragoza['Distrito'] == 'Oliver - Valdefierro', 'Distrito'] = 'Oliver-Valdefierro'
distritos_zaragoza.loc[distritos_zaragoza['Distrito'] == 'Actur - Rey Fernando', 'Distrito'] = 'Actur-Rey Fernando'
distritos_zaragoza.loc[distritos_zaragoza['Distrito'] == 'Juslibol - El Zorongo', 'Distrito'] = 'Juslibol-El Zorongo'

# Creo columna llamada ciudad, con el nombre de la misma:
distritos_zaragoza['Ciudad'] = 'Zaragoza'

distritos_zaragoza


None
CRS no definido. Por favor, definir el CRS establecido en origen: 25830
El CRS de origen es: EPSG:25830


CRS incorrecto, EPSG:25830, lo transformamos a EPSG: 4326
CRS actualizado, EPSG:4326


Distrito  \
0   Torrecilla de Valmadrid   
1           La Cartuja Baja   
2            Torrero-La Paz   
3                Casablanca   
4                       Sur   
5                  San José   
6               Universidad   
7               Las Fuentes   
8                    Centro   
9                  Delicias   
10       Oliver-Valdefierro   
11          Casco Histórico   
12               Miralbueno   
13                   Movera   
14             Santa Isabel   
15                 El Rabal   
16              La Almozara   
17       Actur-Rey Fernando   
18         Venta del Olivar   
19             San Gregorio   
20              Monzalbarba   
21                Montañana   
22                  Casetas   
23   San Juan de Mozarrifar   
24            Garrapinillos   
25               Villarrapa   
26                  Alfocea   
27                 Peñaflor   
28      Juslibol-El Zorongo   

                                             geometry    Ciudad  
0   POLYGON ((-0.85959 41.51766, -0.85888 41.51742...  Zaragoza  
1   POLYGON ((-0.84666 41.62559, -0.8457 41.62512,...  Zaragoza  
2   POLYGON ((-0.8894 41.63372, -0.88849 41.63361,...  Zaragoza  
3   POLYGON ((-0.91417 41.64002, -0.91411 41.63988...  Zaragoza  
4   POLYGON ((-0.94378 41.6409, -0.94294 41.6407, ...  Zaragoza  
5   POLYGON ((-0.87229 41.64622, -0.87226 41.6462,...  Zaragoza  
6   POLYGON ((-0.89361 41.6465, -0.89359 41.64638,...  Zaragoza  
7   POLYGON ((-0.86219 41.65288, -0.85921 41.65199...  Zaragoza  
8   POLYGON ((-0.89163 41.65223, -0.89098 41.65147...  Zaragoza  
9   POLYGON ((-0.9188 41.65867, -0.91748 41.65823,...  Zaragoza  
10  POLYGON ((-0.92409 41.65927, -0.92361 41.659, ...  Zaragoza  
11  POLYGON ((-0.88694 41.65958, -0.88574 41.65917...  Zaragoza  
12  POLYGON ((-0.96945 41.66821, -0.96904 41.66812...  Zaragoza  
13  POLYGON ((-0.84105 41.67082, -0.84054 41.67071...  Zaragoza  
14  POLYGON ((-0.81122 41.67858, -0.81047 41.6785,...  Zaragoza  
15  POLYGON ((-0.85973 41.67961, -0.85817 41.67946...  Zaragoza  
16  POLYGON ((-0.91066 41.6817, -0.90949 41.68159,...  Zaragoza  
17  POLYGON ((-0.86989 41.69378, -0.86945 41.69353...  Zaragoza  
18  POLYGON ((-0.97404 41.69729, -0.97368 41.69703...  Zaragoza  
19  POLYGON ((-0.86263 41.70593, -0.86216 41.70544...  Zaragoza  
20  POLYGON ((-0.96504 41.72219, -0.96374 41.72163...  Zaragoza  
21  POLYGON ((-0.80708 41.72726, -0.80709 41.72696...  Zaragoza  
22  POLYGON ((-1.07474 41.73837, -1.07344 41.73785...  Zaragoza  
23  POLYGON ((-0.85941 41.74041, -0.85915 41.74034...  Zaragoza  
24  POLYGON ((-1.12458 41.74776, -1.1244 41.74768,...  Zaragoza  
25  POLYGON ((-1.10362 41.75719, -1.10367 41.7571,...  Zaragoza  
26  POLYGON ((-0.97418 41.76396, -0.97405 41.76378...  Zaragoza  
27  POLYGON ((-0.79634 41.79693, -0.79623 41.79684...  Zaragoza  
28  POLYGON ((-0.95816 41.93124, -0.9572 41.93108,...  Zaragoza

Donosti

In [14]:
distritos_donosti = gpd.read_file('/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/02.Distritos/Contornos/Shapefile/donosti/distritos_donosti.shp')
distritos_donosti

# Configuro CRS
# CRS por defecto en descarga: 25830
distritos_donosti = definicion_crs (distritos_donosti)

# Me quedo con la columna que alberga los distritos y la que alberga la geometría:
distritos_donosti = distritos_donosti[['NomDisMun', 'geometry']]
# Renmobro columa 'nombre' a distrito:
distritos_donosti = distritos_donosti.rename(columns={'NomDisMun': 'Distrito'})
# Transformo valores de Columna distrito, de todo mayúsculas a solo letra inicial:
distritos_donosti['Distrito'] = distritos_donosti['Distrito'].str.title()
# Creo columna llamada ciudad, con el nombre de la misma:
distritos_donosti['Ciudad'] = 'San Sebastian'

distritos_donosti

CRS no definido. Por favor, definir el CRS establecido en origen: 25830
El CRS de origen es: EPSG:25830


CRS incorrecto, EPSG:25830, lo transformamos a EPSG: 4326
CRS actualizado, EPSG:4326


Distrito                                           geometry  \
0             Este  POLYGON ((-1.91398 43.29631, -1.91399 43.29628...   
1  Centro Nordeste  POLYGON ((-1.94552 43.32832, -1.94552 43.32829...   
2       Centro Sur  POLYGON ((-1.94023 43.29256, -1.94025 43.29251...   
3            Oeste  MULTIPOLYGON (((-1.95675 43.29101, -1.95696 43...   

          Ciudad  
0  San Sebastian  
1  San Sebastian  
2  San Sebastian  
3  San Sebastian

Málaga

In [15]:
distritos_malaga = gpd.read_file('/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/02.Distritos/Contornos/Shapefile/malaga/distritos_malaga.shp')
distritos_malaga

# Configuro CRS
# CRS por defecto en descarga: 4326
distritos_malaga = definicion_crs (distritos_malaga)

# Me quedo con la columna que alberga los distritos y la que alberga la geometría:
distritos_malaga = distritos_malaga[['NOMBRE', 'geometry']]
# Renmobro columa 'nombre' a distrito:
distritos_malaga = distritos_malaga.rename(columns={'NOMBRE': 'Distrito'})
# Transformo valores de Columna distrito, de todo mayúsculas a solo letra inicial:
distritos_malaga['Distrito'] = distritos_malaga['Distrito'].str.title()

# Modifico valores de los mismos, para que coincidan en procesos posteriores:
distritos_malaga.loc[distritos_malaga['Distrito'] == 'Carretera De Cadiz', 'Distrito'] = 'Carretera de Cádiz'
distritos_malaga.loc[distritos_malaga['Distrito'] == 'Cruz De Humilladero', 'Distrito'] = 'Cruz de Humilladero'
distritos_malaga.loc[distritos_malaga['Distrito'] == 'Bailen-Miraflores', 'Distrito'] = 'Bailén-Miraflores'
distritos_malaga.loc[distritos_malaga['Distrito'] == 'Ciudad Jardin', 'Distrito'] = 'Ciudad Jardín'
distritos_malaga.loc[distritos_malaga['Distrito'] == 'Puerto De La Torre', 'Distrito'] = 'Puerto de la Torre'

# Creo columna llamada ciudad, con el nombre de la misma:
distritos_malaga['Ciudad'] = 'Málaga'

distritos_malaga

CRS correcto, EPSG:4326


Distrito                                           geometry  \
0              Churriana  POLYGON Z ((-4.51628 36.69605 0.00004, -4.5159...   
1     Carretera de Cádiz  POLYGON Z ((-4.43052 36.71173 0.00004, -4.4299...   
2   Teatinos-Universidad  POLYGON Z ((-4.50119 36.71986 0.00004, -4.4972...   
3    Cruz de Humilladero  POLYGON Z ((-4.45845 36.72532 0.00004, -4.4583...   
4      Bailén-Miraflores  POLYGON Z ((-4.44648 36.74137 0.00004, -4.4464...   
5         Palma-Palmilla  POLYGON Z ((-4.46609 36.84946 0.00004, -4.4658...   
6          Ciudad Jardín  POLYGON Z ((-4.37231 36.89221 0.00004, -4.3723...   
7                   Este  MULTIPOLYGON Z (((-4.28342 36.77315 0.00004, -...   
8                 Centro  POLYGON Z ((-4.41453 36.69873 0.00004, -4.4152...   
9     Puerto de la Torre  POLYGON Z ((-4.46756 36.81662 0.00004, -4.4677...   
10           Campanillas  POLYGON Z ((-4.50284 36.79429 0.00004, -4.5026...   

    Ciudad  
0   Málaga  
1   Málaga  
2   Málaga  
3   Málaga  
4   Málaga  
5   Málaga  
6   Málaga  
7   Málaga  
8   Málaga  
9   Málaga  
10  Málaga

UNIFICADO

In [16]:
# Combino los distintos geodataframes creados en los puntos anteriores, aprovechando que tienen el mismo nombre de columna,
# obteniendo un geodataframe único que facilitará las posteriores líneas de código.
distritos_ciudades = pd.concat(
    [
        distritos_valencia,
        distritos_madrid,
        distritos_barcelona,
        distritos_sevilla,
        distritos_bilbao,
        distritos_zaragoza,
        distritos_donosti,
        distritos_malaga
    ]
    , ignore_index=True)

distritos_ciudades.info()
distritos_ciudades

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 116 entries, 0 to 115
Data columns (total 3 columns):
 #   Column    Non-Null Count  Dtype   
---  ------    --------------  -----   
 0   Distrito  116 non-null    object  
 1   geometry  116 non-null    geometry
 2   Ciudad    116 non-null    object  
dtypes: geometry(1), object(2)
memory usage: 2.8+ KB


Distrito                                           geometry  \
0      Poblats Del Nord  POLYGON ((-0.31988 39.56171, -0.31953 39.56214...   
1            Benimaclet  POLYGON ((-0.35489 39.47809, -0.36274 39.48389...   
2              Campanar  POLYGON ((-0.42651 39.495, -0.42612 39.49507, ...   
3      Poblats Maritims  POLYGON ((-0.33151 39.48561, -0.3315 39.48561,...   
4             La Saïdia  POLYGON ((-0.38947 39.48856, -0.38692 39.48916...   
..                  ...                                                ...   
111       Ciudad Jardín  POLYGON Z ((-4.37231 36.89221 0.00004, -4.3723...   
112                Este  MULTIPOLYGON Z (((-4.28342 36.77315 0.00004, -...   
113              Centro  POLYGON Z ((-4.41453 36.69873 0.00004, -4.4152...   
114  Puerto de la Torre  POLYGON Z ((-4.46756 36.81662 0.00004, -4.4677...   
115         Campanillas  POLYGON Z ((-4.50284 36.79429 0.00004, -4.5026...   

       Ciudad  
0    Valencia  
1    Valencia  
2    Valencia  
3    Valencia  
4    Valencia  
..        ...  
111    Málaga  
112    Málaga  
113    Málaga  
114    Málaga  
115    Málaga  

[116 rows x 3 columns]

In [ ]:
# Lo guardo como un geojson, en la ruta de drive:
file_path = '/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/02.Distritos/distritos_ciudades.geojson'
distritos_ciudades.to_file(file_path, driver='GeoJSON')

# Tambien como csv por tenerlo:
file_path = '/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/02.Distritos/distritos_ciudades.csv'
distritos_ciudades.to_csv(file_path, index=False)

##### Carga de latitudes y longitudes de los alojamientos

Cargamos el dataset con los alojamientos obtenidos de escrapear la web Airbnb. En las columnas Latitud y Longitud queda definia la ubicación de los mismos.

Ya está cargado en los puntos anteriores, pues ya se han hecho transformaciones con él previamente. Es el df_limpieza
(este punto solo era para la realización individual del punto)

In [ ]:
# alojamientos_df = pd.read_csv('/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/df_AIRBNB.csv')
# alojamientos_df.info()
# alojamientos_df.sample(5)

##### Conversión de latitudes y longitudes a Geodataframe

El siguiente paso es convertir el dataframe de Airbnb a Geodataframe, asegurando que las coordenadas se encuentren en CRS.
Para ello, debo crear antes una lista de puntos geográficos a partir de las coordenadas de latitud y longitud de dicho dataframe, la cual llamamos geometry:

In [17]:
puntos = [Point(xy) for xy in zip(df_limpieza['Longitud'], df_limpieza['Latitud'])]

# Zip combina las dos columnas en pares de coordenadas, por ejemplo [ (long_1, lat_1), (long_2, lat_2)]
# Point crea un objeto tipo Point para cada par de (X, Y): Point (Lat_1, Long_1), etc
# (Point es una clase de la librería Shapely que Geopandas usa para representar puntos geográficos)
# Con ello obtengo geometry, una lista de puntos Point para todas las filas del Datafrme: [Point(Long1, Lat1), Point(Long2,Lat2), etc]

Una vez ya he definido los puntos vía Point, ya puedo convertir el df a tipo geodataframe, indicando el CRS como EPSG:4326.
Para continuar con la misma nomenclatura y no añadir nombres de más, seguiremos llamándolo df_limpieza!

In [18]:
df_limpieza = gpd.GeoDataFrame(df_limpieza, geometry=puntos, crs="EPSG:4326")

##### Unión espacial entre conjuntos (Spatial Join)

Una vez tengo ya el dataframe de alojamientos reconvertido a geodataframe, y los archivos con los distritos unificados a uno solo (con las transformaciones previas que han sido precisas), procedemos a hacer la union espacial entre los dos conjuntos con el fin de asignar a cada alojamiento el distrito en el que se encuentra (basandonos en los puntos que representan los alojamientos, y los polígonos que representan los distritos, todos ellos georreferenciados).

In [19]:
df_limpieza = gpd.sjoin(df_limpieza, distritos_ciudades, how="left", predicate="intersects")

# how=left es el tipo de unión espacial. El resultado incluye todas las filas del gdf puntos, y añade la info de distritos bcn cuando intersecten
# Si un punto no cae en ningún distrito tendrá valores NaN para las columnas que vengan del gdf distritos

# predicate =intersects define la relacion espacial que se busca entre geometrías de los dos gdfs. En este caso, intersects
# implica que las geometrías se combinan si se tocan, superponen o está dentro. Por lo tanto, los puntos se asignarán al polígono del distrito en el que estén dentro.
# Y con ello la info relativa al mismo.

In [20]:
df_limpieza.info()
df_limpieza.sample(5)

<class 'geopandas.geodataframe.GeoDataFrame'>
Index: 7360 entries, 0 to 7359
Data columns (total 27 columns):
 #   Column               Non-Null Count  Dtype   
---  ------               --------------  -----   
 0   URL                  7360 non-null   object  
 1   Nombre Alojamiento   7360 non-null   object  
 2   Descripcion          7360 non-null   object  
 3   Latitud              7360 non-null   float64 
 4   Longitud             7360 non-null   float64 
 5   Rating Limpieza      7360 non-null   object  
 6   Rating Veracidad     7360 non-null   object  
 7   Rating Llegada       7360 non-null   object  
 8   Rating Comunicacion  7360 non-null   object  
 9   Rating Ubicacion     7360 non-null   object  
 10  Rating Calidad       7360 non-null   object  
 11  Servicios            7360 non-null   object  
 12  accommodates         7360 non-null   int64   
 13  bathrooms            7360 non-null   int64   
 14  bedrooms             7360 non-null   int64   
 15  beds              

URL  \
7332             https://www.airbnb.es/rooms/54179590   
969               https://www.airbnb.es/rooms/1858381   
2142   https://www.airbnb.es/rooms/563477456525755602   
1270  https://www.airbnb.es/rooms/1294074284880249958   
5349  https://www.airbnb.es/rooms/1331773125085773036   

                                     Nombre Alojamiento  \
7332                                       Casa Andrade   
969       apart  Artekale,Casco viejo ,parking opcional   
2142  El apartamento más bonito y limpio en una zona...   
1270                                      Embajadores 4   
5349          Amazing apartment in Palos de la Frontera   

                                       Descripcion   Latitud  Longitud  \
7332    Ni hay traducción ni encuentra descripción  42.44386  -8.63964   
969   Hay traducción pero no encuentra descripción  43.25580  -2.92360   
2142  Hay traducción pero no encuentra descripción  40.44127  -3.66199   
1270  Hay traducción pero no encuentra descripción  40.40970  -3.70590   
5349    Ni hay traducción ni encuentra descripción  37.22980  -6.89810   

     Rating Limpieza Rating Veracidad Rating Llegada Rating Comunicacion  \
7332             4.4              4.6            4.7                 4.4   
969              4.9              4.9            5.0                 4.9   
2142             4.7              4.8            4.9                 5.0   
1270             5.0              5.0            5.0                 5.0   
5349           Nuevo            Nuevo          Nuevo               Nuevo   

     Rating Ubicacion Rating Calidad  \
7332              4.6            4.7   
969               5.0            4.8   
2142              4.8            4.8   
1270              5.0            4.7   
5349            Nuevo          Nuevo   

                                              Servicios  accommodates  \
7332  {'Persianas o cortinas opacas', 'Extintor de i...             8   
969   {'Frigorífico', 'Perchas', 'Utensilios básicos...             4   
2142  {'Servicios básicos', 'Wifi', 'Agua caliente',...             4   
1270  {'Frigorífico', 'Calefacción radiante', 'Perch...             2   
5349  {'Frigorífico', 'Televisión de alta definición...             2   

      bathrooms  bedrooms  beds              Fecha registro  \
7332          1         4     4  2025-02-06 01:40:22.035402   
969           1         2     3  2025-01-12 21:36:37.925898   
2142          1         2     4  2025-01-13 10:58:17.865258   
1270          1         1     2  2025-01-13 00:27:48.251946   
5349          1         1     1  2025-01-21 13:28:41.913060   

                                   Título  \
7332            Apartamento en Pontevedra   
969                 Apartamento en Bilbao   
2142             Apartamento en Salamanca   
1270                Apartamento en Madrid   
5349  Apartamento en Palos de la Frontera   

                                                Título2 Precio por noche  \
7332                                       Casa Andrade            99 €    
969       apart  Artekale,Casco viejo ,parking opcional            89 €    
2142  El apartamento más bonito y limpio en una zona...           107 €    
1270                                      Embajadores 4            93 €    
5349          Amazing apartment in Palos de la Frontera            74 €    

                                           Calificación                   ID  \
7332  Valoración media de 4,57 sobre 5, 7 evaluacion...             54179590   
969   Valoración media de 4,88 sobre 5, 528 evaluaci...              1858381   
2142  Valoración media de 4,8 sobre 5, 170 evaluacio...   563477456525755602   
1270                            Alojamiento nuevo Nuevo  1294074284880249958   
5349                            Alojamiento nuevo Nuevo  1331773125085773036   

          Ciudad_left                   geometry  index_right   Distrito  \
7332       Pontevedra  POINT (-8.63964 42.44386)          NaN        NaN   
969   Vitoria-gasteiz    POINT

In [21]:
# Hago unas ligeras transformaciones:
# Elimino ciudaddes right, y renombro ciudades_left, a ciudades:
df_limpieza = df_limpieza.drop(columns=['Ciudad_right'])
df_limpieza = df_limpieza.rename(columns={'Ciudad_left': 'Ciudad'})


In [22]:
df_limpieza.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
Index: 7360 entries, 0 to 7359
Data columns (total 26 columns):
 #   Column               Non-Null Count  Dtype   
---  ------               --------------  -----   
 0   URL                  7360 non-null   object  
 1   Nombre Alojamiento   7360 non-null   object  
 2   Descripcion          7360 non-null   object  
 3   Latitud              7360 non-null   float64 
 4   Longitud             7360 non-null   float64 
 5   Rating Limpieza      7360 non-null   object  
 6   Rating Veracidad     7360 non-null   object  
 7   Rating Llegada       7360 non-null   object  
 8   Rating Comunicacion  7360 non-null   object  
 9   Rating Ubicacion     7360 non-null   object  
 10  Rating Calidad       7360 non-null   object  
 11  Servicios            7360 non-null   object  
 12  accommodates         7360 non-null   int64   
 13  bathrooms            7360 non-null   int64   
 14  bedrooms             7360 non-null   int64   
 15  beds              

##### Comprobación de resultados

In [23]:
# Me quedo con los registros que tienen la columna Distrito no nulo, ya que puede haber registros de otras ciudades de las que no he cargado sus contornos
geodf_compr = df_limpieza.loc[df_limpieza['Distrito'].notna()]
geodf_compr.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
Index: 4303 entries, 31 to 6826
Data columns (total 26 columns):
 #   Column               Non-Null Count  Dtype   
---  ------               --------------  -----   
 0   URL                  4303 non-null   object  
 1   Nombre Alojamiento   4303 non-null   object  
 2   Descripcion          4303 non-null   object  
 3   Latitud              4303 non-null   float64 
 4   Longitud             4303 non-null   float64 
 5   Rating Limpieza      4303 non-null   object  
 6   Rating Veracidad     4303 non-null   object  
 7   Rating Llegada       4303 non-null   object  
 8   Rating Comunicacion  4303 non-null   object  
 9   Rating Ubicacion     4303 non-null   object  
 10  Rating Calidad       4303 non-null   object  
 11  Servicios            4303 non-null   object  
 12  accommodates         4303 non-null   int64   
 13  bathrooms            4303 non-null   int64   
 14  bedrooms             4303 non-null   int64   
 15  beds             

In [25]:
# Llamamos a las columnas de URL, nombre alojamiento, ciudad y distrito:
geodf_compr = geodf_compr[['URL', 'Nombre Alojamiento', 'Ciudad', 'Distrito']]

# Compruebo con muestras aleatorias (mediante google maps) que el distrito asociado es el correcto
geodf_compr.sample(5)

URL  \
4560  https://www.airbnb.es/rooms/1330222218645850121   
5787  https://www.airbnb.es/rooms/1283461422627972739   
88     https://www.airbnb.es/rooms/622383404284336821   
131    https://www.airbnb.es/rooms/545602057442226577   
2790             https://www.airbnb.es/rooms/27020422   

                                     Nombre Alojamiento     Ciudad  \
4560  Wifi/aire acondicionado en el centro del casco...  Barcelona   
5787                              Casa del Guadalquivir    Sevilla   
88    Habitación Hierro en la zona más cool de Valencia   Valencia   
131            Acogedora habitación en Barcelona Centro  Barcelona   
2790               Bergamot House Habitación Individual   Valencia   

            Distrito  
4560    Ciutat Vella  
5787   Casco Antiguo  
88        L'Eixample  
131   Sants-Montjuïc  
2790    Ciutat Vella

##### Guardado de archivo resultante

In [ ]:
df_limpieza.to_csv('/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/df_limpieza.csv', index=False)

###4- EDA

#### 4.0. Carga de csv y librerías

In [ ]:
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objects as go

#Cargamos el fichero para el EDA
df_limpieza = pd.read_csv('/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/df_limpieza.csv')

# Nos quedamos con las ciudad que nos interesan
df_Airbnb_EDA = df_limpieza[df_limpieza['Ciudad'].isin(['Madrid', 'Barcelona', "Valencia"])]
df_Airbnb_EDA.to_csv('/content/drive/MyDrive/White_Hosting/02.Scrapeo_Airbnb/df_Airbnb_EDA.csv', index=False)

#### 4.1 Información General

In [ ]:
df_Airbnb_EDA.info()

In [ ]:
# Cantidad de nulos según columna
df_Airbnb_EDA.isnull().sum()

Todos los nulos están en los ratings y columnas asociadas (valoración media y número de evaluaciones), los cuales provienen de anuncios que aunque tienen evaluaciones no son las suficientes como para reflejar ratios.

#### 4.2. Tipos de alojamiento según ciudad

In [ ]:
conteo_alojamientos = df_Airbnb_EDA.pivot_table(
    index='Ciudad', #Filas
    columns='Tipo_alojamiento_agrupado', #Columnas
    aggfunc='size', #informacion size, que es el tamaño o conteo
    fill_value=0 #Sin decimales, 0 decimales
)
conteo_alojamientos.reset_index()


La ciudad  tanto con más apartamentos enteros como habitaciones privadas es Madrid.

In [ ]:
# Graficamos la información anterior

conteo_alojamientos = df_Airbnb_EDA.groupby(['Ciudad', 'Tipo_alojamiento_agrupado']).size().reset_index(name='count')

color_map = {
    'Entire home/apt': 'blue',
    'Private room': 'green',
    'Shared room': 'orange',
    'Hotel room': 'red'
}

fig = px.bar(conteo_alojamientos,
             x='Ciudad',  # Diferenciamos por Ciudad
             y='count',  # Precio en el eje Y
             color ='Tipo_alojamiento_agrupado',
             color_discrete_map = color_map,
             barmode = 'group',
             title='Tipología y número de alojamientos según ciudad',
             text_auto = True,
             labels={'count': 'Nº Alojamientos', 'Ciudad': 'Ciudad','Tipo_alojamiento_agrupado':'Tipo Alojamiento'},  # Etiquetas personalizadas
             width=1000,
             height=500)

# Personalizamos el gráfico
fig.update_layout(
    yaxis_title='Nº Alojamientos'
)

# Mostramos la gráfica
fig.show()

#### 4.3 Ratings y precio/noche medios según ciudad

In [ ]:
# Promedio de ratings y calificación por ciudad y precio
precio_ratings_ciudad = df_Airbnb_EDA.groupby('Ciudad')[['Precio_noche','Rating_Limpieza', 'Rating_Veracidad', 'Rating_Llegada', 'Rating_Comunicacion', 'Rating_Ubicacion', 'Rating_Calidad', 'Valoración_media']].mean().round(2).reset_index()
precio_ratings_ciudad

Llama la atención el precio medio en Barcelona, muy superior a Madrid y Valencia. La valoraciones son muy similares en las tres ciudades.

#### 4.4 Ratings medios y cantidad total de alojamientos según tipología

In [ ]:
# Agrupar por 'Tipo_alojamiento_agrupado' y calcular los promedios y el conteo
tipo_alojamiento_info = df_Airbnb_EDA.groupby('Tipo_alojamiento_agrupado').agg({
                        'Tipo_alojamiento_agrupado': 'count',
                        'Precio_noche': 'mean',
                        'Valoración_media': 'mean',
                        'Rating_Limpieza': 'mean',
                        'Rating_Veracidad': 'mean',
                        'Rating_Llegada': 'mean',
                        'Rating_Comunicacion': 'mean',
                        'Rating_Ubicacion': 'mean',
                        'Rating_Calidad': 'mean'
}).rename(columns={'Tipo_alojamiento_agrupado': 'count_alojamientos'}).sort_values(by='count_alojamientos', ascending=False).reset_index().round(2)

tipo_alojamiento_info

El tipo de alojamiento "Entire home/apt" es el más común y también el más caro con diferencia. Con una valoración ligeramente menor respecto el resto, encontramos las habitaciones compartidas.

#### 4.5 Precio por noche según ciudad y tipo de alojamiento




In [ ]:
# Agrupar por 'Ciudad' y aplicar describe() a la columna 'Precio_noche'
descripcion_precio_noche = df_Airbnb_EDA.groupby('Ciudad')['Precio_noche'].describe().reset_index().round(2)

descripcion_precio_noche

In [ ]:
fig = px.bar(conteo_alojamientos,
             x='Ciudad',  # Diferenciamos por Ciudad
             y='count',  # Precio en el eje Y
             color ='Tipo_alojamiento_agrupado', #Con el color generamos un segundo agrupamiento
             color_discrete_map = color_map,
             barmode = 'group',
             title='Tipología y número de alojamientos según ciudad',
             text_auto = True,
             labels={'count': 'Nº Alojamientos', 'Ciudad': 'Ciudad','Tipo_alojamiento_agrupado':'Tipo Alojamiento'},  # Etiquetas personalizadas
             width=1000,
             height=500)

# Personalizamos el gráfico, en este caso el eje Y
fig.update_layout(yaxis_title='Nº Alojamientos')
# Mostramos la gráfica
fig.show()

print("\n") #Añadimos un salto para que no se mezclen las gráficas

orden_ciudades= ['Barcelona','Madrid','Valencia']
# Diagrama de bigotes del precio por ciudad
fig = px.box(df_Airbnb_EDA,
             x='Ciudad',  # Diferenciamos por Ciudad
             y='Precio_noche',  # Precio en el eje Y
             color ='Tipo_alojamiento_agrupado', #Con el color generamos un segundo agrupamiento
             color_discrete_map = color_map,
             title='Distribución del Precio por Ciudad según tipo de alojamiento',
             labels={'Precio_noche': 'Precio (€)', 'Ciudad': 'Ciudad','Tipo_alojamiento_agrupado':'Tipo Alojamiento'},  # Etiquetas personalizadas
             width=1000,
             height=500,
             category_orders={'Ciudad': orden_ciudades}
             )

fig.update_layout(yaxis_title='Precio (€)')
# Mostramos la gráfica
fig.show()


En las 3 ciudades se repite el mismo patrón de precios: lo más caro es alquilar un apartamento entero, seguido de una habitación de hotel, la habitación privada, y por último, el compartir habitación; lo cual tiene todo el sentido.

Así mismo, especialmente para los casos de apartamentos enteros, distinguimos un gran número de outliers. Una posible hipótesis, a falta de un análisis detallado, es que estos valores pueden deberse a que se tratan de alojamientos más lujosos o con mejores características con respecto a las que tienen apartamentos más convencionales.  

#### 4.6 Precio según servicios

**Cercanía a la playa**


In [ ]:
# Agrupar por 'Serv_internet' y 'Ciudad', luego calcular size de'Precio_noche', para saber cantidad de anuncios.
cercania_playa = df_Airbnb_EDA.groupby(['Serv_playa', 'Ciudad']).size().round(2).reset_index().sort_values(by="Ciudad").rename(columns={0: 'Total Alojamientos'})
# Mostrar el resultado
cercania_playa

Tanto en Valencia como Barcelona, la cantidad de alojamientos cercanos a la playa es considerablemente menor.

In [ ]:
# Agrupar por 'Serv_playa' y 'Ciudad', luego calcular la media de 'Precio_noche'
precio_playa = df_Airbnb_EDA.groupby(['Serv_playa', 'Ciudad'])['Precio_noche'].mean().round(2).reset_index().sort_values(by="Ciudad")
# Mostrar el resultado.
precio_playa


En las ciudades con playa los precios medios de alojarse son menores en caso de tener cercanía a la misma (1 = SÍ)

In [ ]:
# Diagrama de bigotes del precio por ciudad

color_map = {
    0: 'red',
    1: 'green'
}

fig = px.box(df_Airbnb_EDA,
             x='Ciudad',  # Diferenciamos por Ciudad
             y='Precio_noche',  # Precio en el eje Y
             color ='Serv_playa',
             color_discrete_map = color_map,
             title='Distribución del Precio por Ciudad según cercanía a playa',
             labels={'Precio_noche': 'Precio (€)', 'Ciudad': 'Ciudad','Serv_playa':'Cercanía playa'},  # Etiquetas personalizadas
             width=1000,
             height=500,
             category_orders={'Ciudad': orden_ciudades}
             )
# Personalizamos el gráfico
fig.update_layout(
    yaxis_title='Precio (€)'
)
# Mostramos la gráfica
fig.show()

**Disponibilidad de internet**

In [ ]:
# Agrupar por 'Serv_internet' y 'Ciudad', luego calcular size de'Precio_noche', para saber cantidad de anuncios.
disponibilidad_internet = df_Airbnb_EDA.groupby(['Serv_internet', 'Ciudad']).size().round(2).reset_index().sort_values(by="Ciudad").rename(columns={0: 'Total Alojamientos'})
# Mostrar el resultado
disponibilidad_internet


La inmensa mayoría de los alojamientos ofrecen servicio de internet.

In [ ]:
# Agrupar por 'Serv_internet' y 'Ciudad', luego calcular la media de 'Precio_noche'
precio_internet = df_Airbnb_EDA.groupby(['Serv_internet', 'Ciudad'])['Precio_noche'].mean().round(2).reset_index().sort_values(by="Ciudad")
# Mostrar el resultado
precio_internet

Vemos que el promedio del precio noche es mayor en caso de contar con internet , especialmente en Valencia y Barcelona, siendo en este último casi el doble.

In [ ]:
# Diagrama de bigotes del precio por ciudad

color_map = {
    0: 'red',
    1: 'green'
}

fig = px.box(df_Airbnb_EDA,
             x='Ciudad',  # Diferenciamos por Ciudad
             y='Precio_noche',  # Precio en el eje Y
             color ='Serv_internet',
             color_discrete_map = color_map,
             title='Distribución del Precio por Ciudad, según disponibilidad de WIFI',
             labels={'Precio_noche': 'Precio (€)', 'Ciudad': 'Ciudad','Serv_internet':'Servicio Internet'},  # Etiquetas personalizadas
             width=1000,
             height=500,
             category_orders={'Ciudad': orden_ciudades}
             )

# Personalizamos el gráfico
fig.update_layout(
    yaxis_title='Precio (€)'
)

# Mostramos la gráfica
fig.show()

**Servicio de Parking**

In [ ]:
# Agrupar por 'Serv_piscina' y 'Ciudad', luego calcular la cantidad de anuncios por medio de size en 'Precio_noche'
disponibilidad_parking = df_Airbnb_EDA.groupby(['Serv_parking', 'Ciudad']).size().round(2).reset_index().sort_values(by="Ciudad").rename(columns={0: 'Total Alojamientos'})
# Mostrar el resultado
disponibilidad_parking

En las 3 ciudades hay más alojamientos con disponibilidad de aparcamiento que sin.

In [ ]:
# Agrupar por 'Serv_parking' y 'Ciudad', luego calcular la media de 'Precio_noche'
precio_parking = df_Airbnb_EDA.groupby(['Serv_parking', 'Ciudad'])['Precio_noche'].mean().round(2).reset_index().sort_values(by="Ciudad")
# Mostrar el resultado
precio_parking

Vemos que el promedio del precio los alojamientos que tiene aparcamiento, gratis o de pago, es mayor en Barcelona y Valencia, pero no en Madrid.

In [ ]:
# Diagrama de bigotes del precio por ciudad
fig = px.box(df_Airbnb_EDA,
             x='Ciudad',  # Diferenciamos por Ciudad
             y='Precio_noche',  # Precio en el eje Y
             color ='Serv_parking',
             title='Distribución del Precio por Ciudad, según presencia de parking',
             color_discrete_map = color_map,
             labels={'Precio_noche': 'Precio (€)', 'Ciudad': 'Ciudad','Serv_parking':'Parking'},  # Etiquetas personalizadas
             width=1000,
             height=500,
             category_orders={'Ciudad': orden_ciudades}
             )

# Personalizamos el gráfico
fig.update_layout(
    yaxis_title='Precio (€)'
)

# Mostramos la gráfica
fig.show()

**Disponibilidad de Piscina**

In [ ]:
# Agrupar por 'Serv_piscina' y 'Ciudad', luego calcular la cantidad de anuncios por medio de size en 'Precio_noche'
disponibilidad_piscina = df_Airbnb_EDA.groupby(['Serv_piscina', 'Ciudad']).size().round(2).reset_index().sort_values(by="Ciudad").rename(columns={0: 'Total Alojamientos'})
# Mostrar el resultado
disponibilidad_piscina

En las 3 ciudades, la mayor parte de los alojamientos no ofrecen servicio de piscina

In [ ]:
# Agrupar por 'Serv_piscina y 'Ciudad', luego calcular la media de 'Precio_noche'
precio_piscina = df_Airbnb_EDA.groupby(['Serv_piscina', 'Ciudad'])['Precio_noche'].mean().round(2).reset_index().sort_values(by="Ciudad")
# Mostrar el resultado
precio_piscina


De media, el precio por noche es algo mayor en los alojamientos que sí ofrecen este servicio, encontrándose la mayor diferencia en Valencia.

In [ ]:
# Diagrama de bigotes del precio por ciudad
fig = px.box(df_Airbnb_EDA,
             x='Ciudad',  # Diferenciamos por Ciudad
             y='Precio_noche',  # Precio en el eje Y
             color ='Serv_piscina',
             color_discrete_map=color_map,
             title='Distribución del Precio por Ciudad, según disponibilidad de piscina',
             labels={'Precio_noche': 'Precio (€)', 'Ciudad': 'Ciudad','Serv_piscina':'Servicio Piscina'},  # Etiquetas personalizadas
             width=1000,
             height=500,
             category_orders={'Ciudad': orden_ciudades}
             )

# Personalizamos el gráfico
fig.update_layout(
    yaxis_title='Precio (€)'
)

# Mostramos la gráfica
fig.show()